### Create the intermediate layer for the Air Travel warehouse



#### Create BQ dataset for storing the intermediate data

In [ ]:
from google.cloud import bigquery

project_id = "cs378-fa2024"
dataset = "air_travel_int"
region = "us-central1"

bq_client = bigquery.Client()

dataset_id = bigquery.Dataset(f"{project_id}.{dataset}")
dataset_id.location = region
resp = bq_client.create_dataset(dataset_id, exists_ok=True)
print("Created dataset {}.{}".format(bq_client.project, resp.dataset_id))

Created dataset cs378-fa2024.air_travel_int


#### `Airport` table (anomaly 9)

##### Goal: come up with a universal airport identifier. Intuitively, we would like to use the IATA code because it is the one that most people are familiar with. The problem is that this code is not globally unique, and we would need to pair it up with the country where the airport is located.

##### Instead of `{iata, country}`, we will use the ICAO code, which is globally unique. Unfortunately, there are many records in the airports table which are missing an icao code. We will attempt to use the LLM to look them up, but we need to watch out for hallucinations.

##### We want to end up with distinct airports in the table and only airports. We will remove all other records from the table, including duplicate airports and non-airports.

##### Once the aiport table is ready, we will re-create the child tables so that they reference the new airport identifier.


##### Before creating the new Airport table, we want to see if we can enrich it with the airport state. This data is not in the airports staging table, but it's  available from the `tsa_traffic` table (for US airports only).

In [ ]:
%%bigquery
select distinct a.airport_id, a.icao, a.iata, a.airport_name, a.city, a.country, t.airport_state
from air_travel_stg.airports a
left join air_travel_stg.tsa_traffic t
on a.iata = t.airport_code
where a.country = 'United States'
and t.airport_state is not null

Query is running:   0%|          |

Downloading:   0%|          |

airport_id  icao iata                                airport_name  \
0         5959  PADK  ADK                                Adak Airport   
1         4064  KSGU  SGU                 St George Municipal Airport   
2         4064  KSGU  SGU                 St George Municipal Airport   
3         4338  KCEZ  CEZ                    Cortez Municipal Airport   
4         4344  KCOD  COD                Yellowstone Regional Airport   
..         ...   ...  ...                                         ...   
362       6133  KPSC  PSC                          Tri Cities Airport   
363       3582  KLGB  LGB        Long Beach /Daugherty Field/ Airport   
364       3817  KSMF  SMF            Sacramento International Airport   
365       4101  KMFR  MFR  Rogue Valley International Medford Airport   
366       3807  KRNO  RNO            Reno Tahoe International Airport   

             city        country airport_state  
0     Adak Island  United States            AK  
1    Saint George  United States            UT  
2    Saint George  United States            LA  
3          Cortez  United States            CO  
4            Cody  United States            WY  
..            ...            ...           ...  
362         Pasco  United States            WA  
363    Long Beach  United States            CA  
364    Sacramento  United States            CA  
365       Medford  United States            OR  
366          Reno  United States            NV  

[367 rows x 7 columns]

##### Note: icao code KSGU should not be appearing twice. This is a problem.

In [ ]:
%%bigquery
select * from air_travel_stg.tsa_traffic
where airport_code = 'SGU'

Query is running:   0%|          |

Downloading:   0%|          |

event_date hour airport_code          airport_name airport_city  \
0  2023-11-08   12          SGU    St George Regional   St. George   
1  2024-03-13   12          SGU    St George Regional   St. George   
2  2024-07-24   12          SGU    St George Regional   St. George   
3  2024-03-20   12          SGU    St George Regional   St. George   
4  2022-08-17   12          SGU  St. George Municipal   St. George   
5  2023-06-21    6          SGU  St. George Municipal   St. George   
6  2023-02-15   12          SGU   Shreveport Regional   Shreveport   

  airport_state    tsa_checkpoint  passenger_count  
0            UT              SGUZ               82  
1            UT              SGUZ               44  
2            UT              SGUZ               58  
3            UT              SGUZ               33  
4            UT              SGUZ               62  
5            UT              SGUZ               30  
6            LA  Checkpoint SHV01               71

###### Note: Shreveport Regional was assigned the wrong iata code, should be SHV instead of SGU

In [ ]:
%%bigquery
select icao, count(*) as duplicate_icao_records
from
(select distinct a.airport_id, a.icao, a.iata, a.airport_name, a.city, a.country, t.airport_state
from air_travel_stg.airports a
left join air_travel_stg.tsa_traffic t
on a.iata = t.airport_code
where a.country = 'United States'
and t.airport_state is not null)
group by icao
having count(*) > 1

Query is running:   0%|          |

Downloading:   0%|          |

icao  duplicate_icao_records
0   KSGU                       2
1   KCNY                       2
2   KCPR                       2
3   KGRB                       2
4   KAMA                       2
5   KBRD                       2
6   KSHV                       2
7   KSHD                       2
8   KATL                       2
9   KPKB                       2
10  KCRW                       2
11  KLWB                       2
12  KHTS                       2
13  KLBE                       2
14  PANC                       2
15  KFAT                       2

##### Want to leave out the above icao codes because they are associated with more than one state in the tsa_traffic table and one of the two values is wrong and we don't know which one.

In [4]:
%%bigquery
create or replace table air_travel_int.duplicate_icao as
  select icao
  from
    (select distinct a.airport_id, a.icao, a.iata, a.airport_name, a.city, a.country, t.airport_state
    from air_travel_stg.airports a
    left join air_travel_stg.tsa_traffic t
    on a.iata = t.airport_code
    where a.country = 'United States'
    and t.airport_state is not null)
  group by icao
  having count(*) > 1

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Create the Airport table in three statements, first add US airports with state values, then add the remaining US airports without states and lastly add non-US airports.

In [5]:
%%bigquery
create or replace table air_travel_int.Airport as
  select distinct a.icao, a.iata, a.airport_name as name,
      a.city, tsa.airport_state as state, a.country,
      a.latitude, a.longitude, a.altitude, a.timezone_name, a.timezone_delta, a.daylight_savings_time,
      a.type, a.source
  from air_travel_stg.airports a
  left join air_travel_stg.tsa_traffic tsa
  on a.iata = tsa.airport_code
  where a.country = 'United States'
  and a.type in ('airport', 'unknown', NULL)
  and a.icao not in (select icao from air_travel_int.duplicate_icao)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [6]:
%%bigquery
insert into air_travel_int.Airport
(icao, iata, name, city, country, latitude, longitude, altitude,
timezone_name, timezone_delta, daylight_savings_time, type, source)
select icao, iata, airport_name, city, country, latitude, longitude, altitude, timezone_name,
        timezone_delta, daylight_savings_time, type, source
from air_travel_stg.airports
where country = 'United States'
and type in ('airport', 'unknown', NULL)
and icao in (select icao from air_travel_int.duplicate_icao)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [7]:
%%bigquery
select count(*) airports_us_only
from air_travel_int.Airport

Query is running:   0%|          |

Downloading:   0%|          |

airports_us_only
0              1569

In [8]:
%%bigquery
insert into air_travel_int.Airport
(icao, iata, name, city, country, latitude, longitude, altitude,
timezone_name, timezone_delta, daylight_savings_time, type, source)
select icao, iata, airport_name, city, country, latitude, longitude, altitude, timezone_name,
        timezone_delta, daylight_savings_time, type, source
from air_travel_stg.airports
where country != 'United States'
and type in ('airport', 'unknown', NULL)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [9]:
%%bigquery
select count(*) as airports_non_us
from air_travel_int.Airport
where country != 'United States'

Query is running:   0%|          |

Downloading:   0%|          |

airports_non_us
0             7619

In [10]:
%%bigquery
select count(*) as airports_total
from air_travel_int.Airport

Query is running:   0%|          |

Downloading:   0%|          |

airports_total
0            9188

##### Look at the records missing icao codes

In [ ]:
%%bigquery
select * except(latitude, longitude, altitude, timezone_name, timezone_delta, daylight_savings_time)
from air_travel_int.Airport
where icao is null
order by name

Query is running:   0%|          |

Downloading:   0%|          |

icao  iata                            name                     city  \
0     None  None                          12APO               12 Apostles   
1     None  None                           ABNER  Abner Range - Lost City   
2     None  None                      AGAP South               AGAP South   
3     None  None                           ANTFR               St. John's   
4     None  None                           ANTFR               St. John's   
...    ...   ...                             ...                      ...   
1233  None  None                          Zurich                   Zurich   
1234  None  None  Zurich Airport Railway Station                   Kloten   
1235  None  None                       Zurich-HB                   Zurich   
1236  None  None                    Zweibruecken             Zweibruecken   
1237  None  None                       \'t Harde                Oldebroek   

     state              country     type source _data_source  \
0     None            Australia  unknown   User  openflights   
1     None            Australia  unknown   User  openflights   
2     None           Antarctica  unknown   User  openflights   
3     None  Antigua and Barbuda  unknown   User  openflights   
4     None  Antigua and Barbuda  unknown   User  openflights   
...    ...                  ...      ...    ...          ...   
1233  None          Switzerland  unknown   User  openflights   
1234  None          Switzerland  airport   User  openflights   
1235  None          Switzerland  unknown   User  openflights   
1236  None              Germany  unknown   User  openflights   
1237  None          Netherlands  unknown   User  openflights   

                           _load_time  
0    2024-08-25 15:58:56.032055+00:00  
1    2024-08-25 15:58:56.032055+00:00  
2    2024-08-25 15:58:56.032055+00:00  
3    2024-08-25 15:58:56.032055+00:00  
4    2024-08-25 15:58:56.032055+00:00  
...                               ...  
1233 2024-08-25 15:58:56.032055+00:00  
1234 2024-08-25 15:58:56.032055+00:00  
1235 2024-08-25 15:58:56.032055+00:00  
1236 2024-08-25 15:58:56.032055+00:00  
1237 2024-08-25 15:58:56.032055+00:00  

[1238 rows x 10 columns]

In [ ]:
%%bigquery
select count(*) as missing_iata
from air_travel_int.Airport
where iata is null

Query is running:   0%|          |

Downloading:   0%|          |

missing_iata
0          2759

##### Call LLM
##### Use gemini to fill in the missing icao and other empty values in a record. Also, determine if the null and unknown records are real airports, want to remove them from the table if they aren't airports.

In [ ]:
import vertexai
from vertexai.generative_models import GenerativeModel, Part

project_id = "cs378-fa2024"
region = "us-central1"
model_name = "gemini-1.5-flash-001"
prompt = """Here is a list of ids and names.
I want you to check if the name corresponds to a real airport. If it does, return the original id and name along with the icao code, iata code, city, state or province, and country.
Return the results as json.
For example,
{"name": "Los Angeles International Airport": "icao": "KLAX", "iata": "LAX", "city": "Los Angelos", "state": "CA", "country": "United States"},
{"name": "Adak Airport": "icao": "PADK", "iata": "ADK", "city": "Adak Island", "state": "AK", "country": "United States"}
Don't return the records which are not valid airports.

Below is the list of names:
"Los Angeles International Airport, United States"
"Adak Airport, United States"
"""

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)
resp = model.generate_content([prompt])
resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
print(resp_text)

[  {    "name": "Los Angeles International Airport, United States",    "icao": "KLAX",    "iata": "LAX",    "city": "Los Angeles",    "state": "CA",    "country": "United States"  },  {    "name": "Adak Airport, United States",    "icao": "PADK",    "iata": "ADK",    "city": "Adak",    "state": "AK",    "country": "United States"  }] 


##### Refine the prompt, adding instructions and making it more dynamic. Also, send small batches to the LLM to reduce hallucinations

In [11]:
import itertools, json, pandas, pandas_gbq
from google.cloud import bigquery
import vertexai
from vertexai.generative_models import GenerativeModel, Part

project_id = "cs378-fa2024"
region = "us-central1"
model_name = "gemini-1.5-flash-001"
prompt = """Here is a list of names.
I want you to check if the name corresponds to a real airport. If it is, return the original name and country, along with the icao code, iata code, city, state or province, and country.
Return the results as a properly formatted json object with only one json object per line.
Return only one answer per airport.
Don't return the records which are not airports.
Don't return any empty json objects.
Don't return an explanation for your answer.
Here are some sample runs:

I pass you:
"Los Angeles International Airport, United States"
"Adak Airport, United States"

You return:
{"name": "Los Angeles International Airport", "icao": "KLAX", "iata": "LAX", "city": "Los Angelos", "state": "CA", "country": "United States"}
{"name": "Adak Airport", "icao": "PADK", "iata": "ADK", "city": "Adak Island", "state": "AK", "country": "United States"}
"""
sql = """select distinct name, country from air_travel_int.Airport
where icao is null and name is not null and country is not null"""

bq_client = bigquery.Client()
rows = bq_client.query_and_wait(sql)
vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)

batch_size = 30    # send 30 airport names at a time
record_counter = 0
airport_str = ""
airports = []
for row in rows:
    record_counter += 1
    if record_counter == 1:
        airport_str = f"{row['name']},{row['country']}"
    else:
        airport_str += f"\n {row['name']},{row['country']}"

    if record_counter == batch_size:
        airports.append(airport_str)
        airport_str = ""
        record_counter = 0

print(f"{len(airports)} batches will be sent to LLM")
#print("airports are:", airports)

# send records to LLM and save results to airport_tmp table
table_id = "air_travel_int.airport_tmp"

for i, records in enumerate(airports):
    first_airport = records.split(",")[0]
    print(f"{i}: batch starting with airport {first_airport}")

    resp = model.generate_content([records, prompt])
    resp_text = resp.text.replace("```json", "").replace("```", "")
    #print("resp_text:", resp_text)

    json_text = resp_text.split("\n")
    #print("json_text:", json_text)

    json_objs = []

    for json_str in json_text:
        if json_str in (None, ""):
            continue
        else:
            #print("json_str", json_str)
            json_str_clean = json_str.replace("},", "}")

            try:
                json_objs.append(json.loads(json_str))
            except Exception as e:
                print(f"Error converting {json_str} to json:", e)

    print("json_objs:", json_objs)

    try:
        df_raw = pandas.DataFrame(json_objs)
        #print("df_raw", df_raw.to_string())
    except Exception as e:
        print("Error while creating df_raw:", e)
        break

    try:
        df_unique = df_raw.drop_duplicates(subset=["name", "country"], keep="last")
        #print("df_unique", df_unique.to_string())
    except Exception as e:
        print("Error while creating df_unique:", e)
        break
        #print(f"got back {len(df_raw.index)} airports from LLM")

    try:
        if i == 0:
            pandas_gbq.to_gbq(df_unique, table_id, project_id=project_id, if_exists="replace")
        else:
            pandas_gbq.to_gbq(df_unique, table_id, project_id=project_id, if_exists="append")
        #print(f"saved results to {table_id}")
    except Exception as e:
        print("Error while writing to BQ:", e)


38 batches will be sent to LLM
0: batch starting with airport Tambo Int'l. Airport Gautrain Station
json_objs: [{'name': "Tambo Int'l. Airport Gautrain Station", 'icao': 'FALA', 'iata': 'JNB', 'city': 'Johannesburg', 'state': 'Gauteng', 'country': 'South Africa'}, {'name': 'Incheon Airport Cargo Terminal Station', 'icao': 'RKSI', 'iata': 'ICN', 'city': 'Incheon', 'state': 'Incheon', 'country': 'South Korea'}, {'name': 'Flughafen U-Bahn', 'icao': 'EDDM', 'iata': 'MUC', 'city': 'Munich', 'state': 'Bavaria', 'country': 'Germany'}, {'name': 'Gare de Montpellier-Saint-Roch', 'icao': 'LFMT', 'iata': 'MPL', 'city': 'Montpellier', 'state': 'Occitanie', 'country': 'France'}, {'name': 'Busan International Passenger Terminal', 'icao': 'RKPK', 'iata': 'PUS', 'city': 'Busan', 'state': 'South Gyeongsang', 'country': 'South Korea'}, {'name': 'Sydney Domestic Airport Station', 'icao': 'YSSY', 'iata': 'SYD', 'city': 'Sydney', 'state': 'New South Wales', 'country': 'Australia'}, {'name': 'Gare de La Pla

100%|██████████| 1/1 [00:00<00:00, 8355.19it/s]


1: batch starting with airport Dokdo
json_objs: [{'name': 'Haneda Airport International Terminal Station', 'icao': 'RJTT', 'iata': 'HND', 'city': 'Tokyo', 'state': 'Tokyo', 'country': 'Japan'}, {'name': 'Byron Airport', 'icao': 'YBSN', 'iata': 'BYN', 'city': 'Byron Bay', 'state': 'New South Wales', 'country': 'Australia'}, {'name': 'Franz Josef Aerodrome', 'icao': 'NFJZ', 'iata': 'FZJ', 'city': 'Franz Josef', 'state': 'West Coast', 'country': 'New Zealand'}, {'name': 'Songshan Airport Station', 'icao': 'RCTP', 'iata': 'TSA', 'city': 'Taipei', 'state': 'Taipei City', 'country': 'Taiwan'}, {'name': 'Skadovsk', 'icao': 'UKKO', 'iata': 'SKD', 'city': 'Skadovsk', 'state': 'Kherson Oblast', 'country': 'Ukraine'}, {'name': 'Lovosice Hlavni Nad.', 'icao': 'LKLO', 'iata': 'LVA', 'city': 'Lovosice', 'state': 'Ústí nad Labem Region', 'country': 'Czech Republic'}, {'name': 'Kodari Schoolyard Heliport', 'icao': 'VNKO', 'iata': 'KRI', 'city': 'Kodari', 'state': 'Bagmati', 'country': 'Nepal'}]


100%|██████████| 1/1 [00:00<00:00, 7869.24it/s]


2: batch starting with airport Gare de Champagne-Ardenne TGV
json_objs: [{'name': 'Gare de Champagne-Ardenne TGV', 'icao': 'XCR', 'iata': 'XCR', 'city': 'Champagne-Ardenne', 'state': None, 'country': 'France'}, {'name': 'Gare de Celestat', 'icao': 'LFGC', 'iata': 'CGS', 'city': 'Sélestat', 'state': None, 'country': 'France'}, {'name': 'Hot Springs Cove Aerodrome', 'icao': 'CAH8', 'iata': None, 'city': 'Hot Springs Cove', 'state': 'British Columbia', 'country': 'Canada'}, {'name': 'Osloer Strasse', 'icao': None, 'iata': None, 'city': None, 'state': None, 'country': None}, {'name': 'Station', 'icao': None, 'iata': None, 'city': None, 'state': None, 'country': None}, {'name': 'Hardy Reef', 'icao': None, 'iata': None, 'city': None, 'state': None, 'country': None}, {'name': 'TEST', 'icao': None, 'iata': None, 'city': None, 'state': None, 'country': None}, {'name': 'Bryansk Orlovskiy', 'icao': 'UUOO', 'iata': 'BYS', 'city': 'Bryansk', 'state': None, 'country': 'Russia'}, {'name': 'Kuramathi'

...

100%|██████████| 1/1 [00:00<00:00, 8719.97it/s]


36: batch starting with airport Whitehaven Beach
json_objs: [{'name': 'Ambatomainty Airport', 'icao': 'FMNA', 'iata': 'AMY', 'city': 'Ambatomainty', 'state': None, 'country': 'Madagascar'}, {'name': 'Andavadoaka Airport', 'icao': 'FMAV', 'iata': 'AVA', 'city': 'Andavadoaka', 'state': None, 'country': 'Madagascar'}, {'name': 'Gatokae Airport', 'icao': 'AGGT', 'iata': 'GKA', 'city': 'Gatokae', 'state': None, 'country': 'Solomon Islands'}, {'name': 'Kirawira Aerodrome', 'icao': 'HTKR', 'iata': 'KWI', 'city': 'Kirawira', 'state': None, 'country': 'Tanzania'}, {'name': 'Kogatende Airstrip', 'icao': 'HTKD', 'iata': 'KGT', 'city': 'Kogatende', 'state': None, 'country': 'Tanzania'}, {'name': 'Grumeti Airstrip', 'icao': 'HTGU', 'iata': 'GRU', 'city': 'Grumeti', 'state': None, 'country': 'Tanzania'}, {'name': 'Sasakwa Airstrip', 'icao': 'HTSA', 'iata': 'SAS', 'city': 'Sasakwa', 'state': None, 'country': 'Tanzania'}, {'name': 'Mtemere Airstrip', 'icao': 'HTME', 'iata': 'MTE', 'city': 'Mtemere', '

100%|██████████| 1/1 [00:00<00:00, 6820.01it/s]


37: batch starting with airport Ambunti
json_objs: [{'name': 'Wipim Airport', 'icao': 'AYWP', 'iata': 'WIP', 'city': 'Wipim', 'state': 'Milne Bay Province', 'country': 'Papua New Guinea'}, {'name': 'Telefomin Airport', 'icao': 'AYTF', 'iata': 'TFN', 'city': 'Telefomin', 'state': 'Sandaun Province', 'country': 'Papua New Guinea'}, {'name': 'Ononge Airport', 'icao': 'AYON', 'iata': 'ONG', 'city': 'Ononge', 'state': 'New Ireland Province', 'country': 'Papua New Guinea'}, {'name': 'Woitape Airport', 'icao': 'AYWT', 'iata': 'WTP', 'city': 'Woitape', 'state': 'Eastern Highlands Province', 'country': 'Papua New Guinea'}, {'name': 'Bosset Airport', 'icao': 'AYBS', 'iata': 'BOS', 'city': 'Bosset', 'state': 'Western Province', 'country': 'Papua New Guinea'}, {'name': 'Tadji Airport', 'icao': 'AYTJ', 'iata': 'TDJ', 'city': 'Tadji', 'state': 'Madang Province', 'country': 'Papua New Guinea'}, {'name': 'Lake Murray Airport', 'icao': 'AYLM', 'iata': 'LMU', 'city': 'Lake Murray', 'state': 'Southern Hi

100%|██████████| 1/1 [00:00<00:00, 7653.84it/s]


In [12]:
%%bigquery
select *
from air_travel_int.airport_tmp
order by name, country

Query is running:   0%|          |

Downloading:   0%|          |

name  icao  iata         city  \
0                  't Harde Airport  EHTH  None     't Harde   
1                             ANTFR  TDPD   ANU   St. John's   
2                  Aberdeen Airport  EGED   ABZ     Aberdeen   
3                Abu Rudeis Airport  HEAR   ARS   Abu Rudeis   
4                  Achutupo Airport  MPAH   ACH     Achutupo   
..                              ...   ...   ...          ...   
639                             Zoo  None  None         None   
640                  Zurich Airport   ZRH   ZRH       Zurich   
641                  Zurich Airport   ZRH   ZRH       Zurich   
642  Zurich Airport Railway Station  LSZH   ZRH       Zurich   
643                    Zweibruecken  EDRZ   ZQW  Zweibrücken   

                    state              country  
0              Gelderland          Netherlands  
1     Antigua and Barbuda  Antigua and Barbuda  
2                Scotland       United Kingdom  
3                    None                Egypt  
4                  Panama               Panama  
..                    ...                  ...  
639                  None                 None  
640                Zurich          Switzerland  
641                  None          Switzerland  
642                Zurich          Switzerland  
643  Rhineland-Palatinate              Germany  

[644 rows x 6 columns]

##### Check for duplicate records

In [13]:
%%bigquery
  select name, country, count(*) as duplicates
  from air_travel_int.airport_tmp
  group by name, country
  having count(*) > 1

Query is running:   0%|          |

Downloading:   0%|          |

name      country  duplicates
0  Zurich Airport  Switzerland           2

In [14]:
%%bigquery
select * from air_travel_int.airport_tmp
where name = 'Zurich Airport' and country = 'Switzerland'

Query is running:   0%|          |

Downloading:   0%|          |

name icao iata    city   state      country
0  Zurich Airport  ZRH  ZRH  Zurich    None  Switzerland
1  Zurich Airport  ZRH  ZRH  Zurich  Zurich  Switzerland

##### Remove duplicate record

In [16]:
%%bigquery
delete from air_travel_int.airport_tmp
where name = 'Zurich Airport' and country = 'Switzerland'
and state is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Merge `airport_tmp` into `Airport` by joining on airport name and country.



In [17]:
%%bigquery
update air_travel_int.Airport a
set a.icao = t.icao, a.iata = t.iata, a.city = t.city, a.state = t.state
from air_travel_int.airport_tmp t
where a.name = t.name and a.country = t.country
and a.icao is null
and t.icao is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [18]:
%%bigquery
select * from air_travel_int.Airport
where icao is null

Query is running:   0%|          |

Downloading:   0%|          |

icao  iata                       name               city state  \
0    None  None              Kiel Seehafen               Kiel  None   
1    None  None          Cornwall Wallmart  Cornwall Wallmart  None   
2    None  None              Ballon Mathes             Selzen  None   
3    None  None                    Kartaly            Kartaly  None   
4    None   BCP                      Bambu              Bambu  None   
..    ...   ...                        ...                ...   ...   
740  None   RYO                 Rio Turbio         Rio Turbio  None   
741  None  None               Lago Posadas       Lago Posadas  None   
742  None   CVI              Caleta Olivia      Caleta Olivia  None   
743  None  None                   Fitz Roy         El Chalten  None   
744  None  None  Sun Island Resort and SPA   South Aari Atoll  None   

              country                                    latitude  \
0             Germany   54.31725200000000000000000000000000000000   
1              Canada   45.02428000000000000000000000000000000000   
2             Germany   49.85000000000000000000000000000000000000   
3              Russia   53.03348800000000000000000000000000000000   
4    Papua New Guinea   -5.86361110000000000000000000000000000000   
..                ...                                         ...   
740         Argentina  -51.53333300000000000000000000000000000000   
741         Argentina  -47.53333300000000000000000000000000000000   
742         Argentina  -46.43330000000000000000000000000000000000   
743         Argentina  -47.03333300000000000000000000000000000000   
744          Maldives    3.48833400000000000000000000000000000000   

                                      longitude  altitude  \
0     10.13885000000000000000000000000000000000         0   
1    -74.75041000000000000000000000000000000000        40   
2      8.24000000000000000000000000000000000000       250   
3     60.68524300000000000000000000000000000000       670   
4    146.49250000000000000000000000000000000000      6790   
..                                          ...       ...   
740  -72.30000000000000000000000000000000000000      1158   
741  -71.75000000000000000000000000000000000000       748   
742  -67.53330000000000000000000000000000000000       124   
743  -67.25000000000000000000000000000000000000       757   
744   72.86298900000000000000000000000000000000         0   

                      timezone_name  timezone_delta daylight_savings_time  \
0                              None               1                     E   
1                              None              -5                     A   
2                              None               1                     E   
3                              None               4                     N   
4                              None              10                     N   
..                              ...             ...                   ...   
740  America/Argentina/Rio_Gallegos              -3                     N   
741  America/Argentina/Rio_Gallegos              -3                     N   
742  America/Argentina/Rio_Gallegos              -3                     N   
743  America/Argentina/Rio_Gallegos              -3                     N   
744               America/Sao_Paulo              -3                     N   

        type       source  
0    unknown         User  
1    unknown         User  
2    unknown         User  
3    unknown         User  
4    unknown         User  
..       ...          ...  
740  unknown         User  
741  unknown         User  
742  unknown         User  
743  unknown         User  
744  airport  OurAirports  

[745 rows x 14 columns]

##### Delete records which are missing an icao code

In [19]:
%%bigquery
delete from air_travel_int.Airport
where icao is null or icao = ''

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key field


In [20]:
%%bigquery
select icao, count(*) as duplicate_icao
from air_travel_int.Airport
group by icao
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

icao  duplicate_icao
0    RKNY               6
1    LFPG               5
2    LPPT               5
3    EHAM               5
4    RJTT               4
..    ...             ...
183  AYTF               2
184  OMDW               2
185  OMSJ               2
186  OMAA               2
187  OMDB               2

[188 rows x 2 columns]

In [21]:
%%bigquery
select * from air_travel_int.Airport
where icao in
    (select icao
      from air_travel_int.Airport
      group by icao
      having count(*) > 1)
order by icao

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                                     name       city  \
0    AGGT  GKA                          Gatokae Airport    Gatokae   
1    AGGT  NNB                        Santa Ana Airport  Santa Ana   
2    AYGA  GSM                   Gasmata Island Airport    Gasmata   
3    AYGA  GKA                           Goroka Airport     Goroka   
4    AYKK  KKA                           Kokoda Airport     Kokoda   
..    ...  ...                                      ...        ...   
421  ZSPD  PVG    Shanghai Pudong International Airport   Shanghai   
422  ZSSS  SHA                    Airport South Station   Shanghai   
423  ZSSS  SHA  Shanghai Hongqiao International Airport   Shanghai   
424  ZYSQ  YSQ                Songyuan Chaganhu Airport   Songyuan   
425  ZYSQ  DQA                    Daqing Saertu Airport     Daqing   

                state           country  \
0                None   Solomon Islands   
1                None   Solomon Islands   
2    Western Province  Papua New Guinea   
3                None  Papua New Guinea   
4                None  Papua New Guinea   
..                ...               ...   
421              None             China   
422              None             China   
423              None             China   
424              None             China   
425      Heilongjiang             China   

                                       latitude  \
0     -8.75000000000000000000000000000000000000   
1    -10.84799400000000000000000000000000000000   
2     -6.27111000000000000000000000000000000000   
3     -6.08168983459000100000000000000000000000   
4     -8.88468000000000000000000000000000000000   
..                                          ...   
421   31.14340019226074200000000000000000000000   
422   23.38800000000000000000000000000000000000   
423   31.19790077209472700000000000000000000000   
424   44.93811400000000000000000000000000000000   
425   46.58333300000000000000000000000000000000   

                                      longitude  altitude  \
0    158.20000000000000000000000000000000000000         0   
1    162.45410800000000000000000000000000000000         3   
2    150.33100000000000000000000000000000000000        23   
3    145.39199829100000000000000000000000000000      5282   
4    147.73100000000000000000000000000000000000      1240   
..                                          ...       ...   
421  121.80500030517578000000000000000000000000        13   
422  113.29740000000000000000000000000000000000        35   
423  121.33599853515625000000000000000000000000        10   
424  124.55017800000000000000000000000000000000       459   
425  125.00000000000000000000000000000000000000      1020   

            timezone_name  timezone_delta daylight_savings_time     type  \
0     Pacific/Guadalcanal              11                     U  airport   
1     Pacific/Guadalcanal              11                     U  airport   
2    Pacific/Port_Moresby              10                     U  airport   
3    Pacific/Port_Moresby              10                     U  airport   
4    Pacific/Port_Moresby              10                     U  airport   
..                    ...             ...                   ...      ...   
421         Asia/Shanghai               8                     U  airport   
422                  None               8                     U  airport   
423         Asia/Shanghai               8                     U  airport   
424                  None               8                     N  airport   
425         Asia/Shanghai               8                     U  airport   

          source  
0           User  
1    OurAirports  
2           User  
3    OurAirports  
4           User  
..           ...  
421  OurAirports  
422         User  
423  OurAirports  
424  OurAirports  
425         User  

[426 rows x 14 columns]

##### Remove the duplicate records whose `source` = 'User' or `type` = 'unknown'

---



In [22]:
%%bigquery
delete from air_travel_int.Airport
where source = 'User' or type = 'unknown'
and icao in (select icao
             from air_travel_int.Airport
             group by icao
             having count(*) > 1)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [23]:
%%bigquery
select icao, count(*) as duplicate_icao
from air_travel_int.Airport
group by icao
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [icao, duplicate_icao]
Index: []

##### Note: if no duplicates exist, skip the next few steps and go directly to the Cleanup section.

In [ ]:
%%bigquery
select * from air_travel_int.Airport
where icao in
    (select icao
      from air_travel_int.Airport
      group by icao
      having count(*) > 1)
order by icao

Query is running:   0%|          |

Downloading:   0%|          |

airport_id  icao iata                                     name  \
0         6064  AGGT  GTK                          Gatokae Airport   
1         7618  AGGT  NNB                        Santa Ana Airport   
2         5971  AYGA  GSM                   Gasmata Island Airport   
3            1  AYGA  GKA                           Goroka Airport   
4         5976  AYKK  KKA                           Kokoda Airport   
..         ...   ...  ...                                      ...   
138       3406  ZSPD  PVG    Shanghai Pudong International Airport   
139      10712  ZSSS  SHA                    Airport South Station   
140       3391  ZSSS  SHA  Shanghai Hongqiao International Airport   
141       9845  ZYDQ  DQA                           Saertu Airport   
142       6942  ZYDQ  DQA                    Daqing Saertu Airport   

               city         state           country  \
0           Gatokae       Western   Solomon Islands   
1         Santa Ana          None   Solomon Islands   
2    Gasmata Island          None  Papua New Guinea   
3            Goroka          None  Papua New Guinea   
4            Kokoda          None  Papua New Guinea   
..              ...           ...               ...   
138        Shanghai          None             China   
139        Shanghai      Shanghai             China   
140        Shanghai          None             China   
141          Daqing          None             China   
142          Daqing  Heilongjiang             China   

                                       latitude  \
0     -8.75000000000000000000000000000000000000   
1    -10.84799400000000000000000000000000000000   
2     -6.27111000000000000000000000000000000000   
3     -6.08168983459000100000000000000000000000   
4     -8.88468000000000000000000000000000000000   
..                                          ...   
138   31.14340019226074200000000000000000000000   
139   23.38800000000000000000000000000000000000   
140   31.19790077209472700000000000000000000000   
141   46.74638888890000000000000000000000000000   
142   46.58333300000000000000000000000000000000   

                                      longitude  altitude  \
0    158.20000000000000000000000000000000000000         0   
1    162.45410800000000000000000000000000000000         3   
2    150.33100000000000000000000000000000000000        23   
3    145.39199829100000000000000000000000000000      5282   
4    147.73100000000000000000000000000000000000      1240   
..                                          ...       ...   
138  121.80500030517578000000000000000000000000        13   
139  113.29740000000000000000000000000000000000        35   
140  121.33599853515625000000000000000000000000        10   
141  125.14055555600000000000000000000000000000       496   
142  125.00000000000000000000000000000000000000      1020   

            timezone_name  timezone_delta daylight_savings_time     type  \
0     Pacific/Guadalcanal              11                     U  airport   
1     Pacific/Guadalcanal              11                     U  airport   
2    Pacific/Port_Moresby              10                     U  airport   
3    Pacific/Port_Moresby              10                     U  airport   
4    Pacific/Port_Moresby              10                     U  airport   
..                    ...             ...                   ...      ...   
138         Asia/Shanghai               8                     U  airport   
139                  None               8                     U  airport   
140         Asia/Shanghai               8                     U  airport   
141         Asia/Shanghai               8                     N  airport   
142         Asia/Shanghai               8                     U  airport   

          source _data_source                       _load_time  
0           User  openflights 2024-08-25 15:58:56.032055+00:00  
1    OurAirports  openflights 2024-08-25 15:58:56.032055+00:00  
2           User  openflights 2024-08-25 15:58:5

##### Use the LLM to lookup the airport details for the duplicate icao codes. Keep the airport record that matches the LLM one and delete the other copies.

In [ ]:
import itertools, json, pandas, pandas_gbq
from google.cloud import bigquery
import vertexai
from vertexai.generative_models import GenerativeModel, Part

project_id = "cs378-fa2024"
region = "us-central1"
model_name = "gemini-1.5-flash-001"
prompt = """Here is a list of icao codes.
I want you to use the icao code to look up the airport details.
Return the results as a properly formatted json object with only one json object per line.
Return only one answer per airport.
Don't return the records which are not airports.
Don't return any empty json objects.
Don't return an explanation for your answer.
Here are some sample runs:

I pass you:
"PADK"
"KELP"

You return:
{"name": "Adak Airport", "icao": "PADK", "iata": "ADK", "city": "Adak Island", "state": "AK", "country": "United States"}
{"name": "El Paso International Airport", "icao": "KELP", "iata": "ELP", "city": "El Paso", "state": "TX", "country": "United States"}
"""
sql = """select icao
    from air_travel_int.Airport
    group by icao
    having count(*) > 1
"""

bq_client = bigquery.Client()
rows = bq_client.query_and_wait(sql)
vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)

batch_size = 5    # send 5 icao codes at a time
record_counter = 0
airport_str = ""
airports = []
for row in rows:
    record_counter += 1
    if record_counter == 1:
        airport_str = f"{row['icao']}"
    else:
        airport_str += f"\n {row['icao']}"

    if record_counter == batch_size:
        airports.append(airport_str)
        airport_str = ""
        record_counter = 0

print(f"{len(airports)} batches will be sent to LLM")
#print("airports are:", airports)

# send records to LLM and save results to airport_tmp table
table_id = "air_travel_int.icao_tmp"

for i, records in enumerate(airports):
    first_icao = records.split("\n")[0]
    print(f"{i}: batch starting with airport {first_icao}")

    resp = model.generate_content([records, prompt])
    resp_text = resp.text.replace("```json", "").replace("```", "")
    #print("resp_text:", resp_text)

    json_text = resp_text.split("\n")
    #print("json_text:", json_text)

    json_objs = []

    for json_str in json_text:
        if json_str in (None, ""):
            continue
        else:
            #print("json_str", json_str)
            json_str_clean = json_str.replace("},", "}")
            #print("json_str_clean", json_str_clean)
            try:
                json_objs.append(json.loads(json_str))
            except Exception as e:
                print(f"Error converting {json_str} to json:", e)

    #print("json_objs:", json_objs)

    try:
        df_raw = pandas.DataFrame(json_objs)
        #print("df_raw", df_raw.to_string())
    except Exception as e:
        print("Error while creating df_raw:", e)
        break

    try:
        df_unique = df_raw.drop_duplicates(subset=["icao"], keep="last")
        #print("df_unique", df_unique.to_string())
    except Exception as e:
        print("Error while creating df_unique:", e)
        break
        #print(f"got back {len(df_raw.index)} airports from LLM")

    try:
        if i == 0:
            pandas_gbq.to_gbq(df_unique, table_id, project_id=project_id, if_exists="replace")
        else:
            pandas_gbq.to_gbq(df_unique, table_id, project_id=project_id, if_exists="append")
        #print(f"saved results to {table_id}")
    except Exception as e:
        print("Error while writing to BQ:", e)


13 batches will be sent to LLM
0: batch starting with airport CYTZ


100%|██████████| 1/1 [00:00<00:00, 7913.78it/s]


1: batch starting with airport CYMM


100%|██████████| 1/1 [00:00<00:00, 8035.07it/s]


2: batch starting with airport EDDF
Error converting {"name": "Friedrichshafen Airport", "icao": "EDNY", "iata": "FDH", "city": " to json: Unterminated string starting at: line 1 column 76 (char 75)


...

100%|██████████| 1/1 [00:00<00:00, 7612.17it/s]


11: batch starting with airport ZSSS


100%|██████████| 1/1 [00:00<00:00, 8577.31it/s]


12: batch starting with airport HCMK


100%|██████████| 1/1 [00:00<00:00, 8943.08it/s]


In [ ]:
%%bigquery
select * from air_travel_int.icao_tmp

Query is running:   0%|          |

Downloading:   0%|          |

name  icao iata             city  \
0                        Brussels Airport  EBBR  BRU         Brussels   
1              Berlin Brandenburg Airport  EDDB  BER           Berlin   
2           Liverpool John Lennon Airport  EGGP  LPL        Liverpool   
3    Leeds Bradford International Airport  LFSB  LBA            Leeds   
4              Lyon-Saint Exupéry Airport  LFLL  LYS             Lyon   
..                                    ...   ...  ...              ...   
188           Malta International Airport  LMML  MLA             Luqa   
189                      Anguilla Airport  TQPF  AXA       The Valley   
190                        Atyrau Airport  UAAA  ATY           Atyrau   
191     Fort Lauderdale Executive Airport  KFXE  FXE  Fort Lauderdale   
192              Hokkaido Kushiro Airport  HCMK  KUH          Kushiro   

                       state         country  
0    Brussels-Capital Region         Belgium  
1                     Berlin         Germany  
2                 Merseyside  United Kingdom  
3             West Yorkshire  United Kingdom  
4       Auvergne-Rhône-Alpes          France  
..                       ...             ...  
188                     None           Malta  
189                     None        Anguilla  
190                     None      Kazakhstan  
191                       FL   United States  
192                 Hokkaido           Japan  

[193 rows x 6 columns]

In [ ]:
%%bigquery
select * from air_travel_int.Airport where icao = 'CYVR'

Query is running:   0%|          |

Downloading:   0%|          |

airport_id  icao iata                             name       city  \
0       8598  CYVR  YVR                     All Airports  Vancouver   
1       8599  CYVR  YVR                     All Airports  Vancouver   
2        156  CYVR  YVR  Vancouver International Airport  Vancouver   

              state country                                   latitude  \
0  British Columbia  Canada  45.50861100000000000000000000000000000000   
1  British Columbia  Canada  43.65305600000000000000000000000000000000   
2              None  Canada  49.19390106200000000000000000000000000000   

                                     longitude  altitude      timezone_name  \
0   -73.55388900000000000000000000000000000000        53    America/Toronto   
1   -79.38305600000000000000000000000000000000       302    America/Toronto   
2  -123.18399810800000000000000000000000000000        14  America/Vancouver   

   timezone_delta daylight_savings_time     type       source _data_source  \
0              -5                     A  airport         User  openflights   
1              -5                     A  airport         User  openflights   
2              -8                     A  airport  OurAirports  openflights   

                        _load_time  
0 2024-08-25 15:58:56.032055+00:00  
1 2024-08-25 15:58:56.032055+00:00  
2 2024-08-25 15:58:56.032055+00:00

In [ ]:
%%bigquery
select distinct a.*
from air_travel_int.Airport a join air_travel_int.icao_tmp t
on a.name = t.name and a.icao = t.icao and a.iata = t.iata
and a.city = t.city and a.country = t.country
where a.icao in (select icao
                from air_travel_int.Airport
                group by icao
                having count(*) > 1)
order by a.icao

Query is running:   0%|          |

Downloading:   0%|          |

airport_id  icao iata                             name         city state  \
0        156  CYVR  YVR  Vancouver International Airport    Vancouver  None   
1        302  EBBR  BRU                 Brussels Airport     Brussels  None   
2        342  EDDH  HAM                  Hamburg Airport      Hamburg  None   
3        478  EGCC  MAN               Manchester Airport   Manchester  None   
4        495  EGHI  SOU              Southampton Airport  Southampton  None   
5        531  EGPC  WIC                     Wick Airport         Wick  None   

          country                                   latitude  \
0          Canada  49.19390106200000000000000000000000000000   
1         Belgium  50.90140151980000400000000000000000000000   
2         Germany  53.63040161132800000000000000000000000000   
3  United Kingdom  53.35369873046875000000000000000000000000   
4  United Kingdom  50.95029830932617000000000000000000000000   
5  United Kingdom  58.45890045166015600000000000000000000000   

                                     longitude  altitude      timezone_name  \
0  -123.18399810800000000000000000000000000000        14  America/Vancouver   
1     4.48443984985000000000000000000000000000       184    Europe/Brussels   
2     9.98822975158690000000000000000000000000        53      Europe/Berlin   
3    -2.27495002746582030000000000000000000000       257      Europe/London   
4    -1.35679996013641360000000000000000000000        44      Europe/London   
5    -3.09306001663208000000000000000000000000       126      Europe/London   

   timezone_delta daylight_savings_time     type       source _data_source  \
0              -8                     A  airport  OurAirports  openflights   
1               1                     E  airport  OurAirports  openflights   
2               1                     E  airport  OurAirports  openflights   
3               0                     E  airport  OurAirports  openflights   
4               0                     E  airport  OurAirports  openflights   
5               0                     E  airport  OurAirports  openflights   

                        _load_time  
0 2024-08-25 15:58:56.032055+00:00  
1 2024-08-25 15:58:56.032055+00:00  
2 2024-08-25 15:58:56.032055+00:00  
3 2024-08-25 15:58:56.032055+00:00  
4 2024-08-25 15:58:56.032055+00:00  
5 2024-08-25 15:58:56.032055+00:00

##### Delete all the duplicate records which don't have matches in the icao_tmp table

In [ ]:
%%bigquery
delete from air_travel_int.Airport a
where icao in (select icao
                from air_travel_int.Airport
                group by icao
                having count(*) > 1)
and not exists
     (select distinct a.iata, a.name, a.city, a.country
      from air_travel_int.Airport a join air_travel_int.icao_tmp t
      on a.name = t.name and a.icao = t.icao and a.iata = t.iata
      and a.city = t.city and a.country = t.country
      where a.icao in (select icao
                      from air_travel_int.Airport
                      group by icao
                      having count(*) > 1))

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery
select icao, count(*) as duplicate_icao
from air_travel_int.Airport
group by icao
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [icao, duplicate_icao]
Index: []

#### Clean up

In [ ]:
%%bigquery
drop table if exists air_travel_int.airport_tmp;
drop table if exists air_travel_int.icao_tmp;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Now that we have a clean Airport table, we can create all the child tables that reference it. This will resolve anomaly type 9.

#### `TSA_Traffic` table (anomaly type 9)

In [24]:
%%bigquery
select count(*) tsa_stg_records
from air_travel_stg.tsa_traffic

Query is running:   0%|          |

Downloading:   0%|          |

tsa_stg_records
0            10443

In [25]:
%%bigquery
select t.event_date, t.event_hour, a.icao, t.tsa_checkpoint, t.passenger_count
from air_travel_int.Airport a join air_travel_stg.tsa_traffic t
on a.iata = t.airport_code
where a.country = 'United States'

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour  icao tsa_checkpoint  passenger_count
0     2024-03-27          12  PADK    Checkpoint1                7
1     2024-05-08          12  PADK    Checkpoint1               23
2     2023-06-07          12  PADK    Checkpoint1                3
3     2024-07-24          13  PADK    Checkpoint1                1
4     2022-08-17          13  PADK    Checkpoint1               67
...          ...         ...   ...            ...              ...
9597  2023-08-23          13  KFAT         FAT 01              132
9598  2024-07-17          13  KFAT         FAT 01               84
9599  2023-10-11          13  KFAT         FAT 01              190
9600  2017-11-19          17  KFAT         FAT 01               32
9601  2017-11-29          17  KFAT         FAT 01               37

[9602 rows x 5 columns]

In [102]:
%%bigquery
create or replace table air_travel_int.TSA_Traffic as
    select distinct t.event_date, t.event_hour, a.icao as airport_icao, t.tsa_checkpoint, t.passenger_count
    from air_travel_int.Airport a join air_travel_stg.tsa_traffic t
    on a.iata = t.airport_code
    where a.country = 'United States'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [40]:
%%bigquery
select * from air_travel_int.TSA_Traffic

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao           tsa_checkpoint  \
0     2023-10-25        <NA>         KCMH                        A   
1     2023-10-25        <NA>         KCMH                        B   
2     2023-10-25        <NA>         KCMH                        C   
3     2023-03-12        <NA>         KORD                       4B   
4     2023-03-12        <NA>         KORD                       4B   
...          ...         ...          ...                      ...   
9179  2017-11-19          17         KELM          Main Checkpoint   
9180  2017-11-29          17         KELM          Main Checkpoint   
9181  2017-11-29          17         KELP  Consolidated Checkpoint   
9182  2017-11-19          17         KELP  Consolidated Checkpoint   
9183  2017-11-19          17         KELP  Consolidated Checkpoint   

      passenger_count  
0                 246  
1                 338  
2                 181  
3                  13  
4                  19  
...               ...  
9179               30  
9180                7  
9181              234  
9182              494  
9183              128  

[9184 rows x 5 columns]

##### Check for primary key fields for uniqueness

In [41]:
%%bigquery
select event_date, event_hour, airport_icao, tsa_checkpoint, count(*) as count
from air_travel_int.TSA_Traffic
group by event_date, event_hour, airport_icao, tsa_checkpoint
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao           tsa_checkpoint  count
0    2023-12-27          14         KBOI                 BOI-Ckpt     18
1    2023-12-27          14         KBNA              BNA Central     15
2    2024-03-17           0         KLAS               Term 1 - D      4
3    2017-11-26           0         KDTW                    Red 3      3
4    2017-11-26           0         KDEN                    South      3
..          ...         ...          ...                      ...    ...
434  2023-12-27          14         KBOS                       A1      2
435  2023-12-27          14         KBOS                       B1      2
436  2023-12-27          14         KBOS                       B5      2
437  2017-11-29          17         KCLT             E Checkpoint      2
438  2017-11-19          17         KELP  Consolidated Checkpoint      2

[439 rows x 5 columns]

In [42]:
%%bigquery
select * from air_travel_int.TSA_Traffic
where event_date = '2023-12-27'
and event_hour = 14
and airport_icao = 'KBOI'
and tsa_checkpoint = 'BOI-Ckpt'

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao tsa_checkpoint  passenger_count
0   2023-12-27          14         KBOI       BOI-Ckpt                2
1   2023-12-27          14         KBOI       BOI-Ckpt              160
2   2023-12-27          14         KBOI       BOI-Ckpt              125
3   2023-12-27          14         KBOI       BOI-Ckpt              371
4   2023-12-27          14         KBOI       BOI-Ckpt              514
5   2023-12-27          14         KBOI       BOI-Ckpt               58
6   2023-12-27          14         KBOI       BOI-Ckpt               63
7   2023-12-27          14         KBOI       BOI-Ckpt               34
8   2023-12-27          14         KBOI       BOI-Ckpt              506
9   2023-12-27          14         KBOI       BOI-Ckpt              360
10  2023-12-27          14         KBOI       BOI-Ckpt              614
11  2023-12-27          14         KBOI       BOI-Ckpt               36
12  2023-12-27          14         KBOI       BOI-Ckpt              111
13  2023-12-27          14         KBOI       BOI-Ckpt              447
14  2023-12-27          14         KBOI       BOI-Ckpt              368
15  2023-12-27          14         KBOI       BOI-Ckpt              266
16  2023-12-27          14         KBOI       BOI-Ckpt              511
17  2023-12-27          14         KBOI       BOI-Ckpt              720

##### Remove all duplicate records because passenger counts are inconsistent and can't be trusted as is (would require manual work to verify which counts are accurate)

In [103]:
%%bigquery
create or replace table air_travel_int.tsa_traffic_tmp as
    select * from air_travel_int.TSA_Traffic
    where struct(event_date, event_hour, airport_icao, tsa_checkpoint) in
              (select struct(event_date, event_hour, airport_icao, tsa_checkpoint)
                from air_travel_int.TSA_Traffic
                group by event_date, event_hour, airport_icao, tsa_checkpoint
                having count(*) > 1)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [49]:
%%bigquery
select * from air_travel_int.tsa_traffic_tmp
order by event_date, event_hour, airport_icao, tsa_checkpoint

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao        tsa_checkpoint  \
0    2017-11-19           0         KATL       Main Checkpoint   
1    2017-11-19           0         KATL       Main Checkpoint   
2    2017-11-19           0         KDEN                 South   
3    2017-11-19           0         KDEN                 South   
4    2017-11-19           0         KDTW                 Red 3   
..          ...         ...          ...                   ...   
874  2024-06-23           0         PAFA              ASAA-FAI   
875  2024-06-23           0         PANC  F Arrival Checkpoint   
876  2024-06-23           0         PANC  F Arrival Checkpoint   
877  2024-06-23           0         PANC      South Checkpoint   
878  2024-06-23           0         PANC      South Checkpoint   

     passenger_count  
0                 18  
1                 29  
2                134  
3                 16  
4                  9  
..               ...  
874              154  
875                2  
876                6  
877              202  
878              140  

[879 rows x 5 columns]

In [104]:
%%bigquery
select * from air_travel_int.TSA_Traffic
except distinct
select * from air_travel_int.tsa_traffic_tmp

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao           tsa_checkpoint  \
0     2023-10-25        <NA>         KCMH                        A   
1     2023-10-25        <NA>         KCMH                        B   
2     2023-10-25        <NA>         KCMH                        C   
3     2023-03-12        <NA>         KORD                       4B   
4     2023-03-12        <NA>         KORD                       4B   
...          ...         ...          ...                      ...   
8300  2017-11-19          17         KDSM           Main Concourse   
8301  2017-11-29          17         KDSM           Main Concourse   
8302  2017-11-29          17         KELM          Main Checkpoint   
8303  2017-11-19          17         KELM          Main Checkpoint   
8304  2017-11-29          17         KELP  Consolidated Checkpoint   

      passenger_count  
0                 246  
1                 338  
2                 181  
3                  19  
4                  13  
...               ...  
8300              169  
8301               86  
8302                7  
8303               30  
8304              234  

[8305 rows x 5 columns]

In [106]:
%%bigquery
create or replace table air_travel_int.TSA_Traffic as
    (select * from air_travel_int.TSA_Traffic
    except distinct
    select * from air_travel_int.tsa_traffic_tmp)

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Recheck primary key constraint

In [107]:
%%bigquery
select event_date, event_hour, airport_icao, tsa_checkpoint, count(*) as count
from air_travel_int.TSA_Traffic
group by event_date, event_hour, airport_icao, tsa_checkpoint
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

event_date  event_hour airport_icao            tsa_checkpoint  count
0   2023-03-12        <NA>         KORD                        4B      2
1   2023-03-12        <NA>         KONT                        T2      2
2   2023-03-12        <NA>         KSEA                     SCP 3      2
3   2023-03-12        <NA>         KDEN                     South      2
4   2023-03-12        <NA>         KPHX                     T-4 A      2
5   2023-03-12        <NA>         KFAT                    FAT 01      2
6   2023-03-12        <NA>         KEWR                   CKPT-A1      2
7   2023-03-12        <NA>         PAFA                  ASAA-FAI      2
8   2023-03-12        <NA>         KMSP                  South CP      2
9   2023-03-12        <NA>         KMIA                  South-J1      2
10  2023-03-12        <NA>         KJFK                Terminal 1      2
11  2023-03-12        <NA>         KSJC                Terminal A      2
12  2023-03-12        <NA>         KDCA               Concourse A      2
13  2023-03-12        <NA>         KIND              Checkpoint A      2
14  2023-03-12        <NA>         KATL           Main Checkpoint      2
15  2023-03-12        <NA>         KPIT           Main Checkpoint      2
16  2023-03-12        <NA>         PANC          South Checkpoint      2
17  2023-03-12        <NA>         KIAD  Passenger Screening Area      2

##### Delete all records which have a null event hour

In [108]:
%%bigquery
delete from air_travel_int.TSA_Traffic where event_hour is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Recheck primary key fe

In [ ]:
%%bigquery
select event_date, event_hour, airport_icao, tsa_checkpoint, count(*) as count
from air_travel_int.TSA_Traffic
group by event_date, event_hour, airport_icao, tsa_checkpoint
having count(*) > 1
order by count(*) desc

##### Check foreign key constraint (`airport_icao`)

In [53]:
%%bigquery
select count(*) as orphan_records
from air_travel_int.TSA_Traffic
where airport_icao not in (select icao from air_travel_int.Airport)

Query is running:   0%|          |

Downloading:   0%|          |

orphan_records
0               0

In [ ]:
%%bigquery
drop table if exists air_travel_int.tsa_traffic_tmp

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### `Airport_Review` table (data enrichment)

###### Recreate table with icao as the airport identifier (in place of iata)

In [ ]:
%%bigquery
select distinct r.id, r.thread_id, r.airport_code as icao, r.review_date, r.review_author,
  r.review_subject, r.review_body
from air_travel_stg.airport_reviews r join air_travel_int.Airport a
on a.icao = r.airport_code

Query is running:   0%|          |

Downloading:   0%|          |

id  thread_id  icao         review_date  \
0     21134      18493  AGGH 2015-08-18 06:08:46   
1      3896       3257  AK06 2009-06-02 14:57:21   
2      9233       7907  AYMH 2011-08-15 06:17:01   
3      6614        447  AYMN 2010-09-18 20:04:31   
4      8021        447  AYMN 2011-03-20 03:22:10   
...     ...        ...   ...                 ...   
8661  28886      26245  EGPR 2017-12-14 13:56:29   
8662  22060      19419  RPLL 2016-06-09 12:33:38   
8663  22054      19413  RPLL 2016-06-08 15:53:37   
8664  22051      19410  RPLL 2016-06-08 10:10:10   
8665  20046      17405  LFPG 2014-08-08 01:56:13   

                        review_author  \
0                                None   
1                                None   
2                                None   
3                                None   
4                                None   
...                               ...   
8661           FlightinstructorOnline   
8662         Mygoalistotraveltheworld   
8663         Mygoalistotraveltheworld   
8664         Mygoalistotraveltheworld   
8665  SeniorCaptainKevinSeanJiaWenLie   

                                         review_subject  \
0                                               re: HIR   
1                           What is it actually called?   
2                                  Still a good airport   
3                                               re: MDU   
4                                               re: MDU   
...                                                 ...   
8661                               From the Otter pilot   
8662           for Goodluck Mr/Ms. Wont it be difficult   
8663                              sa nagbigay ng advice   
8664  won't it be difficult to pass the immigration ...   
8665                                        My Feedback   

                                            review_body  
0     Reply to @Ozguy: It really needs TLC. Yesterda...  
1     What is the specific name of the Denali Airpor...  
2                                 Still to many rascals  
3     Syphers G C & L A(07) 5445 7968 268 Obi Obi Rd...  
4     Good evening Sypho - remember when you threw t...  
...                                                 ...  
8661  Pilot notes: Find airport info on http://www.n...  
8662  it is Ms :)   Yeah. I have all the documents. ...  
8663  Thanks! :)   Yeah, 14 days tourist visa becaus...  
8664  I will be traveling to Dubai this July 30 dire...  
8665  Quite a cool and creative donut design for T1....  

[8666 rows x 7 columns]

##### Materialize to a temp table

In [10]:
%%bigquery
create or replace table air_travel_int.tmp_airport_reviews as
    select distinct r.id, r.thread_id, r.airport_code as icao, r.date_created, r.author,
        r.subject, r.body
    from air_travel_stg.airport_reviews r join air_travel_int.Airport a
    on a.icao = r.airport_code

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Detect the reviews which refer to an airport and infer the sentiment of such reviews

In [12]:
%%bigquery
select subject, body from air_travel_int.tmp_airport_reviews
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

subject  \
0                      re: HIR   
1  What is it actually called?   
2         Still a good airport   
3                      re: MDU   
4                      re: MDU   
5                      re: MDU   
6                      re: MDU   
7                      re: MDU   
8                          POM   
9         One day soon I hope.   

                                                body  
0  Reply to @Ozguy: It really needs TLC. Yesterda...  
1  What is the specific name of the Denali Airpor...  
2                              Still to many rascals  
3  Reply to @Ozguy: Greetings - I lived there in ...  
4  Syphers G C & L A(07) 5445 7968 268 Obi Obi Rd...  
5  Understand that  one John Rutter is still in t...  
6  Although I do not know Graham, I understand he...  
7  Good evening Sypho - remember when you threw t...  
8  A reasonable international terminal but nothin...  
9  Having spent 2 years living in Rabaul when I w...

In [26]:
import json
import pandas, pandas_gbq
import vertexai
from vertexai.generative_models import GenerativeModel, Part
from google.cloud import bigquery

project_id = "cs378-fa2024"
region = "us-central1"
model_name = "gemini-1.5-flash-001"
prompt = """Go through this list of reviews and determine which ones refer to an airport.
If the review refers to an airport, return relevant = True, otherwise return relevant = False.
Also, detect the tone of the review. Return positive, neutral or negative based on the sentiment.
Return the id along with the relevancy and sentiment for each one.
Format the results as a list of json objects with the schema:
[{id:integer, relevant:boolean, sentiment:string}]
Do not include an explanation with your answer.
"""
llm_input_sql = "select id, subject, body from air_travel_int.tmp_airport_reviews limit 50"

full_table_sql = "select * from air_travel_int.tmp_airport_reviews"


def do_inference(input_str):

    vertexai.init(project=project_id, location=region)
    model = GenerativeModel(model_name)
    resp = model.generate_content([input_str, prompt])
    #print("resp:", resp)
    resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
    print("resp_text:", resp_text)

    results = json.loads(resp_text)

    return results


bq_client = bigquery.Client()
rows = bq_client.query_and_wait(llm_input_sql)

batch_size = 50
reviews = [] # will store the inputs
results = []
combined_results = []

for i, row in enumerate(rows):

    review_str = f"id={row['id']}, subject={row['subject']}, body={row['body']}"
    reviews.append(review_str)

    if i > 0 and i % batch_size == 0:
        # process batch
        print("processing batch")
        reviews_str = '\n'.join(reviews)
        results = do_inference(reviews_str)
        combined_results.extend(results)

        # empty out smaller list before processing next batch
        reviews = []

if len(reviews) > 0:
    print("processing last batch")
    reviews_str = '\n'.join(reviews)
    results = do_inference(reviews_str)
    combined_results.extend(results)

print("combined_results:", combined_results)

df = pandas.DataFrame(combined_results)
print("df:", df.to_string())

table_id = "air_travel_int.tmp_airport_reviews_analyzed" # output table
pandas_gbq.to_gbq(df, table_id, project_id=project_id, if_exists="replace")

processing last batch
resp_text: [  {    "id": 21134,    "relevant": true,    "sentiment": "negative"  },  {    "id": 3896,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 9233,    "relevant": true,    "sentiment": "negative"  },  {    "id": 5115,    "relevant": true,    "sentiment": "positive"  },  {    "id": 6614,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 7500,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 5128,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 8021,    "relevant": true,    "sentiment": "positive"  },  {    "id": 18055,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 16709,    "relevant": true,    "sentiment": "positive"  },  {    "id": 3922,    "relevant": true,    "sentiment": "positive"  },  {    "id": 17609,    "relevant": true,    "sentiment": "positive"  },  {    "id": 17099,    "relevant": true,    "sentiment": "positive"  },  {    "id": 22256,    "relevant": true,    "sentiment":

100%|██████████| 1/1 [00:00<00:00, 5675.65it/s]


##### Join the two tables to inspect the LLM-generated results

In [28]:
%%bigquery
select r.id, r.subject, r.body, a.relevant, a.sentiment
from air_travel_int.tmp_airport_reviews r
join air_travel_int.tmp_airport_reviews_analyzed a
on r.id = a.id

Query is running:   0%|          |

Downloading:   0%|          |

id                                            subject  \
0   21134                                            re: HIR   
1    3896                        What is it actually called?   
2    9233                               Still a good airport   
3    5115                                            re: MDU   
4    6614                                            re: MDU   
5    7500                                            re: MDU   
6    5128                                            re: MDU   
7    8021                                            re: MDU   
8   18055                                                POM   
9   16709                               One day soon I hope.   
10   3922                                       re: Akureryi   
11  17609                                        KEF airport   
12  17099                                                 Hi   
13  22256                                       ZNA location   
14  16249                                     Incorrect link   
15  20486  Short Sighted Municipality - Closing this airp...   
16  19923                          Airport user for 20 years   
17  20757                              This is a total shame   
18  20222                                          Dangerous   
19   5205                                     re: Ice Runway   
20  17619                                  Dunnville Airport   
21  16204                                      Wind Turbines   
22  17497                                      Wind Turbines   
23  17335                                  re: Wind Turbines   
24   8646  pilot rental    sea plane to remote fishing lodge   
25  22969  122.8 is local floatplane frequency and Kenora...   
26  22968  Seaplane base is across from hospital, not whe...   
27  27021                                       (no subject)   
28  50843                                Wally Hare’s Vision   
29  81973                         Flight schools operations?   
30  10021                           Nice Friendly Airport !!   
31  10700                           re: Great Place to Visit   
32  25431                                    What did I see?   
33    905                                       A bit old...   
34   9329                                        The airport   
35  20017                                  Beautiful Airport   
36     80                                        Decent food   
37   9472               Not the prettiest - but the cheapest   
38   8697                                     Up and running   
39  64983                      Frequency missing, please add   
40  21061                                     Flyboys closed   
41   9793                                 Wow what changes!!   
42  16518                                         Unfriendly   
43  24050  Old Bold pilots, Sid and a wonderous field of ...   
44  20709                               Markham Airport CNU8   
45    640                                         Renovating   
46  20866                                       Menu updated   
47  10200                            re: Good place to visit   
48  19021        Airport is beautiful - Restaurant not great   
49  16687                                Collingwood Airport   

                                                 body  relevant sentiment  
0   Reply to @Ozguy: It really needs TLC. Yesterda...      True  negative  
1   What is the specific name of the Denali Airpor...      True   neutral  
2                               Still to many rascals      True  negative  
3   Reply to @Ozguy: Greetings - I lived there in ...      True  positive  
4   Syphers G C & L A(07) 5445 7968 268 Obi Obi Rd...      True   neutral  
5   Understand that  one John Rutter is still in t...      True   neutral  
6   Although I do not know Graham, I understand he...      True   neutral  
7   Good evening Sypho - remember when you threw t...      True  positive  
8   A reasonable international terminal but nothin...     

##### Configure safety settings and process on the full table, using larger batch size

In [41]:
import json
import pandas, pandas_gbq
from google.cloud import bigquery
import vertexai
from vertexai.generative_models import (
    GenerativeModel,
    HarmCategory,
    HarmBlockThreshold,
    Part,
    SafetySetting,
)

project_id = "cs378-fa2024"
region = "us-central1"
model_name = "gemini-1.5-flash-001"
prompt = """Go through this list of reviews and determine which ones refer to an airport.
If the review refers to an airport, return relevant = True, otherwise return relevant = False.
Also, detect the tone of the review. Return positive, neutral or negative based on the sentiment.
Return the id along with the relevancy and sentiment for each one.
Format the results as a list of json objects with the schema:
[{id:integer, relevant:boolean, sentiment:string}]
Do not include an explanation with your answer.
"""
llm_input_sql = "select id, subject, body from air_travel_int.tmp_airport_reviews order by id"

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)

safety_config = [
    SafetySetting(
        category=HarmCategory.HARM_CATEGORY_DANGEROUS_CONTENT,
        threshold=HarmBlockThreshold.BLOCK_ONLY_HIGH,
    ),
]

def do_inference(input_str):

    results = []

    resp = model.generate_content([input_str, prompt], safety_settings=safety_config)
    prompt_token_count = resp.usage_metadata.prompt_token_count
    candidate_token_count = resp.usage_metadata.candidates_token_count

    print("prompt token count:", prompt_token_count)
    print("candidates token count:", candidate_token_count)

    if candidate_token_count == 0 or candidate_token_count == 8192: # 8192 is the output token limit
        # response is either null or truncated, so skip this batch
        return results

    resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
    print("resp_text:", resp_text)

    results = json.loads(resp_text)

    return results

batch_size = 250
start_batch_counter = 0
reviews = [] # for storing the inputs
results = []
combined_results = []

bq_client = bigquery.Client()
rows = bq_client.query_and_wait(llm_input_sql)

for i, row in enumerate(rows):

    review_str = f"id={row['id']}, subject={row['subject']}, body={row['body']}"
    reviews.append(review_str)

    if i > 0 and i % batch_size == 0:
        # process batch
        print(f"processing records {start_batch_counter} - {i}")
        reviews_str = '\n'.join(reviews)
        results = do_inference(reviews_str)

        if len(results) > 0:
            combined_results.extend(results)

        # empty out smaller list before processing next batch
        reviews = []
        start_batch_counter = i + 1

if len(reviews) > 0:
    print(f"processing last batch, starting with record {start_batch_counter}")
    reviews_str = '\n'.join(reviews)
    results = do_inference(reviews_str)

    if len(results) > 0:
        combined_results.extend(results)
        reviews = []

print("combined_results:", combined_results)

df = pandas.DataFrame(combined_results)
print("df:", df.to_string())

table_id = "air_travel_int.tmp_airport_reviews_analyzed" # output table
pandas_gbq.to_gbq(df, table_id, project_id=project_id, if_exists="replace")

processing records 0 - 250
prompt token count: 20332
candidates token count: 7718
resp_text: [  {    "id": 1,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 2,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 3,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 4,    "relevant": true,    "sentiment": "positive"  },  {    "id": 5,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 6,    "relevant": true,    "sentiment": "positive"  },  {    "id": 7,    "relevant": true,    "sentiment": "positive"  },  {    "id": 8,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 9,    "relevant": true,    "sentiment": "positive"  },  {    "id": 10,    "relevant": true,    "sentiment": "positive"  },  {    "id": 11,    "relevant": true,    "sentiment": "neutral"  },  {    "id": 12,    "relevant": true,    "sentiment": "positive"  },  {    "id": 13,    "relevant": true,    "sentiment": "positive"  },  {    "id": 14,    "relevant": true,

100%|██████████| 1/1 [00:00<00:00, 5127.51it/s]


In [42]:
%%bigquery
select r.id, r.subject, r.body, a.relevant, a.sentiment
from air_travel_int.tmp_airport_reviews r
join air_travel_int.tmp_airport_reviews_analyzed a
on r.id = a.id

Query is running:   0%|          |

Downloading:   0%|          |

id                      subject  \
0     3896  What is it actually called?   
1     6614                      re: MDU   
2     7500                      re: MDU   
3     5128                      re: MDU   
4     5205               re: Ice Runway   
...    ...                          ...   
2661  7541            aircraft spotting   
2662  6551        re: New terminal open   
2663  6012                 Chipmunk 035   
2664  6010         Collective Challenge   
2665  9025       Very convenient for me   

                                                   body  relevant sentiment  
0     What is the specific name of the Denali Airpor...      True   neutral  
1     Syphers G C & L A(07) 5445 7968 268 Obi Obi Rd...      True   neutral  
2     Understand that  one John Rutter is still in t...      True   neutral  
3     Although I do not know Graham, I understand he...      True   neutral  
4     Reply to @bcrosby: Also PPR as they have secur...      True   neutral  
...                                                 ...       ...       ...  
2661  aircraft spotting is ausome at this airport ca...      True  positive  
2662  Reply to @david:   this is the best airport an...      True  positive  
2663  I don't know whether it is still there, but Ch...      True  positive  
2664  Spent some time here in autumn 1978 for a heli...      True  positive  
2665  I had a great experience at TLV a few weeks ag...      True  positive  

[2666 rows x 5 columns]

##### Create the final table

In [46]:
%%bigquery
create or replace table air_travel_int.Airport_Review as
    select r.id, r.thread_id, r.icao, r.date_created, r.author, r.subject, r.body, a.relevant, a.sentiment
    from air_travel_int.tmp_airport_reviews r
    left join air_travel_int.tmp_airport_reviews_analyzed a
    on r.id = a.id

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [52]:
%%bigquery
select icao, sentiment, count(*) as count
from air_travel_int.Airport_Review
where relevant = True
group by icao, sentiment
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

icao sentiment  count
0     FKKD  negative    227
1     LPBJ   neutral     24
2     RPLC  negative     21
3     FKKD   neutral     19
4     OPIS   neutral     16
...    ...       ...    ...
1549  LLBG  positive      1
1550  PAEM   neutral      1
1551  KIYK   neutral      1
1552  CYPQ   neutral      1
1553  VAPO  negative      1

[1554 rows x 3 columns]

##### Clean up

In [64]:
%%bigquery
drop table if exists air_travel_int.tmp_airport_reviews;
drop table if exists air_travel_int.tmp_airport_reviews_analyzed;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key field

In [53]:
%%bigquery
select id, count(*) as duplicate_id
from air_travel_int.Airport_Review
group by id
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [id, duplicate_id]
Index: []

##### Check for foreign key violations

In [54]:
%%bigquery
select count(*) as orphan_records
from air_travel_int.Airport_Review
where icao not in (select icao from air_travel_int.Airport)

Query is running:   0%|          |

Downloading:   0%|          |

orphan_records
0               0

#### Create `Airport_Businesses`, `Business`, and `Menu_Items` tables (anomaly types 8, 9, and 10)

##### Decompose `airport_businesses` into `Business` and `Airport_Businesses`. This resolves anomaly type 10.

In [55]:
%%bigquery
select * from air_travel_stg.airport_businesses

Query is running:   0%|          |

Downloading:   0%|          |

airport_code terminal            business            category  \
0             abq        1  Cavalcade of Wings                 Art   
1             cak        1     Huntington Bank                Bank   
2             bdl        1                CNBC                News   
3             psp        1           CNBC News                News   
4             swf        1         Hudson News                News   
...           ...      ...                 ...                 ...   
1569          okc        1                 ATM  Financial Services   
1570          gtr        1                 ATM  Financial Services   
1571          swf        1                 ATM  Financial Services   
1572          dro        1                 ATM  Financial Services   
1573          blv        1                 ATM  Financial Services   

                            location menu_items  _data_source  \
0                       Second Floor       None  airportguide   
1                             Gate 4       None  airportguide   
2                             Gate 3       None  airportguide   
3                             Gate 4       None  airportguide   
4                             Gate 8       None  airportguide   
...                              ...        ...           ...   
1569                    Near Gate B8       None  airportguide   
1570                   Gates B3 & B4       None  airportguide   
1571              Near Baggage Claim       None  airportguide   
1572           Near Gates 11A and 10       None  airportguide   
1573  Level 1 near the main entrance       None  airportguide   

                           _load_time  
0    2024-08-25 15:16:58.467182+00:00  
1    2024-08-25 15:16:58.467182+00:00  
2    2024-08-25 15:16:58.467182+00:00  
3    2024-08-25 15:16:58.467182+00:00  
4    2024-08-25 15:16:58.467182+00:00  
...                               ...  
1569 2024-08-25 15:16:58.467182+00:00  
1570 2024-08-25 15:16:58.467182+00:00  
1571 2024-08-25 15:16:58.467182+00:00  
1572 2024-08-25 15:16:58.467182+00:00  
1573 2024-08-25 15:16:58.467182+00:00  

[1574 rows x 8 columns]

##### Remove some of the noise by getting rid of the obvious entries; things like ticketing, baggage claim, car rental, restrooms, etc.

In [56]:
%%bigquery
select category, business, count(*) as num_businesses
from air_travel_stg.airport_businesses
where category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
group by category, business
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

category             business  num_businesses
0                  News          Hudson News              14
1              Shopping          Hudson News              13
2           Coffee Shop            Starbucks              12
3    Financial Services                  ATM              12
4            Restaurant            Starbucks               9
..                  ...                  ...             ...
843     Beauty Services                Bliss               1
844     Beauty Services             XpresSpa               1
845    Airport Facility               Tables               1
846    Airport Facility  Little Free Library               1
847    Airport Facility     Observation Deck               1

[848 rows x 3 columns]

##### Create the junction table (anomaly 9)

In [57]:
%%bigquery
select distinct a.icao, b.terminal, b.business, b.location
from air_travel_stg.airport_businesses b join air_travel_int.Airport a
on upper(b.airport_code) = a.iata
where a.country = 'United States'
and category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
order by b.business

Query is running:   0%|          |

Downloading:   0%|          |

icao       terminal                    business                location
0     KPSP              1    12th Fairway Bar & Grill                 Gate 11
1     KBOI              1   13th Street Pub and Grill  Near gates B15 and B17
2     KPIE              1  3 Daughters Brewing at PIE                  Gate 2
3     KSFO              2              49 Mile Market             Concourse D
4     KLGB              1                    4th Vine           Near Gates G2
...    ...            ...                         ...                     ...
1029  KLAS              1                      iCandy      Terminal 1 Level 1
1030  KHOU              1                      iStore               Gates 1-4
1031  KSFO              1                      iStore      Near Gates B2 - B4
1032  KBDL              1                      iStore             Gates 15-16
1033  KLAX  international             iStore Boutique           Near Gate 136

[1034 rows x 4 columns]

In [58]:
%%bigquery
create or replace table air_travel_int.Airport_Businesses as
    select distinct a.icao, b.terminal, b.business, b.location
    from air_travel_stg.airport_businesses b join air_travel_int.Airport a
    on upper(b.airport_code) = a.iata
    where a.country = 'United States'
    and category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
    and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
    order by b.business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Double-check uniqueness of primary key fields

In [59]:
%%bigquery
select icao, terminal, business, location, count(*) as count
from air_travel_int.Airport_Businesses
group by icao, terminal, business, location
order by count(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

icao       terminal                    business                location  \
0     KPSP              1    12th Fairway Bar & Grill                 Gate 11   
1     KBOI              1   13th Street Pub and Grill  Near gates B15 and B17   
2     KPIE              1  3 Daughters Brewing at PIE                  Gate 2   
3     KSFO              2              49 Mile Market             Concourse D   
4     KLGB              1                    4th Vine           Near Gates G2   
...    ...            ...                         ...                     ...   
1029  KLAS              1                      iCandy      Terminal 1 Level 1   
1030  KHOU              1                      iStore               Gates 1-4   
1031  KSFO              1                      iStore      Near Gates B2 - B4   
1032  KBDL              1                      iStore             Gates 15-16   
1033  KLAX  international             iStore Boutique           Near Gate 136   

      count  
0         1  
1         1  
2         1  
3         1  
4         1  
...     ...  
1029      1  
1030      1  
1031      1  
1032      1  
1033      1  

[1034 rows x 5 columns]

##### Create new Business entity from `air_travel_stg.airport_businesses`

In [60]:
%%bigquery
select distinct business as name, category, menu_items
from air_travel_stg.airport_businesses
where category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
order by category, business

Query is running:   0%|          |

Downloading:   0%|          |

name          category menu_items
0                      BVLGARI       Accessories       None
1            Beads on the Vine       Accessories       None
2        Brighton Collectibles       Accessories       None
3                        Coach       Accessories       None
4                  NYS Eyewear       Accessories       None
..                         ...               ...        ...
900              Parking Kiosk    Transportation       None
901  Parking Pay on Foot Kiosk    Transportation       None
902       Shuttle Waiting Area    Transportation       None
903           Vending Machines  Vending Machines       None
904                 Smart Park           parking       None

[905 rows x 3 columns]

In [61]:
%%bigquery
create or replace table air_travel_int.tmp_business as
    select distinct business as name, category, menu_items
    from air_travel_stg.airport_businesses
    where category not in ('Ticketing', 'Airlines', 'Airline', 'Airport Services', 'Car Rental', 'Cargo Services', 'Baggage Service', 'Baggage Services', 'Services', 'Air Transportation', 'Airline Ticketing', 'Security', 'Management', 'Airline Services', 'Customer Service', 'Administration', 'Other', 'Vacant', 'Government Services', 'Mail Services', 'Airport Security', 'Immigration', 'Information', 'Parking', 'Police Services', 'Public Space', 'Restrooms', 'Seating', 'Observation Point')
    and business not in ('Restaurant', 'Restaurant Pre-Security', 'Restaurant Post-Security', 'Drinking Water', 'Food & Beverage', 'Restaurant-Bar', 'Snacks and drinks')
    order by business

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check for uniqueness of primary key field, `name`

In [62]:
%%bigquery
select distinct name, count(*) as num_duplicates
from air_travel_int.tmp_business
group by name
having count(*) > 1
order by num_duplicates desc

Query is running:   0%|          |

Downloading:   0%|          |

name  num_duplicates
0               Starbucks              15
1             Burger King               6
2   Einstein Bros. Bagels               6
3           Auntie Anne's               5
4                  Subway               5
..                    ...             ...
68                   Vino               2
69                Wendy's               2
70  Wolfgang Puck Express               2
71        World Duty Free               2
72                 iStore               2

[73 rows x 2 columns]

In [63]:
%%bigquery
select *
from air_travel_int.tmp_business
where name = 'Starbucks'

Query is running:   0%|          |

Downloading:   0%|          |

name     category                                         menu_items
0   Starbucks       Dining                         Coffee,Pastries,Sandwiches
1   Starbucks       Dining  Caramel Macchiato,Pumpkin Spice Latte,Frappuccino
2   Starbucks   Restaurant                       Latte,Cappuccino,Frappuccino
3   Starbucks   Restaurant                                Coffee,Tea,Pastries
4   Starbucks   Restaurant                          Latte,Cappuccino,Espresso
5   Starbucks   Restaurant                         Latte,Frappuccino,Pastries
6   Starbucks   Restaurant                         Coffee,Pastries,Sandwiches
7   Starbucks  Coffee Shop                         Latte,Frappuccino,Espresso
8   Starbucks  Coffee Shop                                Coffee,Tea,Pastries
9   Starbucks  Coffee Shop          Caramel Macchiato,Iced Coffee,Frappuccino
10  Starbucks  Coffee Shop      Caffè Americano,Caramel Macchiato,Frappuccino
11  Starbucks  Coffee Shop                           Latte,Frappuccino,Muffin
12  Starbucks  Coffee Shop                         Latte,Espresso,Frappuccino
13  Starbucks  Coffee Shop                          Latte,Cappuccino,Espresso
14  Starbucks  Coffee Shop  Caramel Macchiato,Pumpkin Spice Latte,Chai Tea...

In [64]:
%%bigquery
select * from air_travel_int.tmp_business
where name = 'Burger King'

Query is running:   0%|          |

Downloading:   0%|          |

name      category                          menu_items
0  Burger King        Dining   Whopper,Chicken Fries,Onion Rings
1  Burger King    Restaurant  Whopper,French Fries,Chicken Fries
2  Burger King    Restaurant       Whopper,Fries,Chicken Nuggets
3  Burger King    Restaurant   Whoppers,Chicken Sandwiches,Fries
4  Burger King  Food & Drink       Whopper,Fries,Chicken Nuggets
5  Burger King  Food & Drink   Whopper,Chicken Fries,Onion Rings

##### Rank by category and menu items in order to remove duplicate businesses

In [66]:
%%bigquery
with sorted_names as
    (select name, category, count(*) as num_businesses
    from air_travel_int.tmp_business
    group by name, category)
select row_number() over (partition by name order by (select num_businesses from sorted_names s where b. category = s.category and b.name = s.name) desc, length(menu_items) desc) AS rank, *
from air_travel_int.tmp_business b
where name in ('Starbucks', 'Burger King')
and menu_items is not null
order by name;

Query is running:   0%|          |

Downloading:   0%|          |

rank         name      category  \
0      1  Burger King    Restaurant   
1      2  Burger King    Restaurant   
2      3  Burger King    Restaurant   
3      4  Burger King  Food & Drink   
4      5  Burger King  Food & Drink   
5      6  Burger King        Dining   
6      1    Starbucks   Coffee Shop   
7      2    Starbucks   Coffee Shop   
8      3    Starbucks   Coffee Shop   
9      4    Starbucks   Coffee Shop   
10     5    Starbucks   Coffee Shop   
11     6    Starbucks   Coffee Shop   
12     7    Starbucks   Coffee Shop   
13     8    Starbucks   Coffee Shop   
14     9    Starbucks    Restaurant   
15    10    Starbucks    Restaurant   
16    11    Starbucks    Restaurant   
17    12    Starbucks    Restaurant   
18    13    Starbucks    Restaurant   
19    14    Starbucks        Dining   
20    15    Starbucks        Dining   

                                           menu_items  
0                  Whopper,French Fries,Chicken Fries  
1                   Whoppers,Chicken Sandwiches,Fries  
2                       Whopper,Fries,Chicken Nuggets  
3                   Whopper,Chicken Fries,Onion Rings  
4                       Whopper,Fries,Chicken Nuggets  
5                   Whopper,Chicken Fries,Onion Rings  
6   Caramel Macchiato,Pumpkin Spice Latte,Chai Tea...  
7       Caffè Americano,Caramel Macchiato,Frappuccino  
8           Caramel Macchiato,Iced Coffee,Frappuccino  
9                          Latte,Frappuccino,Espresso  
10                         Latte,Espresso,Frappuccino  
11                          Latte,Cappuccino,Espresso  
12                           Latte,Frappuccino,Muffin  
13                                Coffee,Tea,Pastries  
14                       Latte,Cappuccino,Frappuccino  
15                         Latte,Frappuccino,Pastries  
16                         Coffee,Pastries,Sandwiches  
17                          Latte,Cappuccino,Espresso  
18                                Coffee,Tea,Pastries  
19  Caramel Macchiato,Pumpkin Spice Latte,Frappuccino  
20                         Coffee,Pastries,Sandwiches

##### Materialize to a temp table

In [67]:
%%bigquery
create or replace table air_travel_int.tmp_business_ranked as
    with sorted_categories as
        (select name, category, count(*) as num_businesses
        from air_travel_int.tmp_business
        group by name, category)
    select row_number() over (partition by name order by (select num_businesses from sorted_categories s where b. category = s.category and b.name = s.name) desc, length(menu_items) desc) AS rank, *
    from air_travel_int.tmp_business b
    where menu_items is not null
    order by name;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Rank the remaining records, the ones which don't have any menu items. Use the popularity of each category to determine the rankings

In [68]:
%%bigquery
select * from air_travel_int.tmp_business
where name in
    (select name
    from air_travel_int.tmp_business
    where menu_items is null
    group by name
    having count(*) > 1)
order by name, category
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

name       category menu_items
0              Book Soup           Shop       None
1              Book Soup       Shopping       None
2  Brighton Collectibles    Accessories       None
3  Brighton Collectibles      Gift Shop       None
4  Brighton Collectibles       Shopping       None
5             Brookstone           Shop       None
6             Brookstone       Shopping       None
7      Broward Duty Free           Shop       None
8      Broward Duty Free       Shopping       None
9                   CNBC  Entertainment       None

In [ ]:
%%bigquery
with (select category, count(*) as num_businesses
      from air_travel_int.tmp_business
      group by category
      order by count(*) desc)

Query is running:   0%|          |

Downloading:   0%|          |

category  num_businesses
0           Restaurant             371
1             Shopping             136
2               Retail               2
3       Bar/Restaurant              30
4         Food & Drink              52
5               Lounge              28
6              Medical               5
7   Financial Services               1
8               Dining              33
9            Gift Shop              24
10                Shop              64
11         Coffee Shop              51
12         Accessories               7
13       Meeting Space               3
14     Beauty Services               5
15      Transportation              13
16              Office               5
17                News              28
18       Entertainment              14
19               Media               2
20                 Art               1
21        Meeting Room               4
22      Duty Free Shop               3
23         Art Exhibit               5
24            Shipping               4
25                Bank               1
26     Beauty Products               1
27    Airport Facility               3
28           Baby Care               1
29       Communication               3
30        Pet Services               1
31             parking               1
32           Newsstand               1
33    Vending Machines               1
34            Clothing               1

In [ ]:
%%bigquery
with sorted_categories as
    (select category, count(*) as num_businesses
    from air_travel_int.tmp_business
    group by category)

select row_number() over (partition by name order by (select num_businesses from sorted_categories s where b. category = s.category) desc) AS rank, *
FROM air_travel_int.tmp_business b
where menu_items is null
and name in ('Book Soup', 'Brighton Collectibles', 'Brookstone', 'Food Court')
order by name;

Query is running:   0%|          |

Downloading:   0%|          |

rank                   name      category menu_items
0     1              Book Soup      Shopping       None
1     2              Book Soup          Shop       None
2     1  Brighton Collectibles      Shopping       None
3     2  Brighton Collectibles     Gift Shop       None
4     3  Brighton Collectibles   Accessories       None
5     1             Brookstone      Shopping       None
6     2             Brookstone          Shop       None
7     1             Food Court    Restaurant       None
8     2             Food Court  Food & Drink       None
9     3             Food Court        Dining       None

In [69]:
%%bigquery
insert into air_travel_int.tmp_business_ranked
with sorted_categories as
    (select category, count(*) as num_businesses
    from air_travel_int.tmp_business
    group by category)

select row_number() over (partition by name order by (select num_businesses from sorted_categories s where b. category = s.category) desc) AS rank, *
from air_travel_int.tmp_business b
where menu_items is null
and name not in (select name from air_travel_int.tmp_business_ranked);

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [70]:
%%bigquery
select * from air_travel_int.tmp_business_ranked
where name in ('Hudson News', 'Food Court')
order by name

Query is running:   0%|          |

Downloading:   0%|          |

rank         name      category menu_items
0     1   Food Court    Restaurant       None
1     2   Food Court  Food & Drink       None
2     3   Food Court        Dining       None
3     1  Hudson News      Shopping       None
4     2  Hudson News          Shop       None
5     3  Hudson News          News       None

##### Check uniqueness of primary key field

In [71]:
%%bigquery
select name, count(*) as count
from air_travel_int.tmp_business_ranked
where rank = 1
group by name
having count(*) > 1
order by count(*) desc

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [name, count]
Index: []

##### Create the final table

In [72]:
%%bigquery
create or replace table air_travel_int.Business as
    select * except(rank)
    from air_travel_int.tmp_business_ranked
    where rank = 1

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Clean up

In [73]:
%%bigquery
drop table air_travel_int.tmp_business;
drop table air_travel_int.tmp_business_ranked;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Add the new `dining<BOOL>` field

In [74]:
%%bigquery
alter table air_travel_int.Business
    add column dining BOOLEAN;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [75]:
%%bigquery
update air_travel_int.Business
    set dining = True where menu_items is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [76]:
%%bigquery
update air_travel_int.Business
    set dining = False where menu_items is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [77]:
%%bigquery
select * from air_travel_int.Business
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name    category  \
0      12th Fairway Bar & Grill  Restaurant   
1     13th Street Pub and Grill  Restaurant   
2    3 Daughters Brewing at PIE  Restaurant   
3                49 Mile Market    Shopping   
4                      4th Vine  Restaurant   
..                          ...         ...   
778          Zoom Travel Stores    Shopping   
779                      eSavvy        Shop   
780                      iCandy        Shop   
781                      iStore    Shopping   
782             iStore Boutique        Shop   

                                menu_items  dining  
0                Sandwiches,Salads,Burgers    True  
1    Pub Burger,Fish & Chips,Chicken Wings    True  
2                       IPA,Stout,Pale Ale    True  
3                                     None   False  
4      Wine,Cheese Plate,Charcuterie Board    True  
..                                     ...     ...  
778                                   None   False  
779                                   None   False  
780                                   None   False  
781                                   None   False  
782                                   None   False  

[783 rows x 4 columns]

##### Split up `menu_items` into individual items, one per row (anomaly type 8)

In [ ]:
%%bigquery
select name, category, menu_items, split(menu_items, ',') as menu_items_array
from air_travel_int.Business
where dining = True

Query is running:   0%|          |

Downloading:   0%|          |

name    category  \
0               Steak 'n' Shake      Dining   
1            Airside Concession      Dining   
2    Nacho Hippo Cantina Maximo      Dining   
3           Landside Concession      Dining   
4              The Iron Compass      Dining   
..                          ...         ...   
412      Jose Cuervo Tequileria  Restaurant   
413                    Loteria!  Restaurant   
414                 Tacos Locos  Restaurant   
415  Earl Campbell's Taco Truck  Restaurant   
416        The Peached Tortilla  Restaurant   

                                        menu_items  \
0             Steakburgers,Milkshakes,French Fries   
1    Burger and Fries,Chicken Sandwich,Pizza Slice   
2                            Nachos,Tacos,Burritos   
3     Breakfast Burrito,Coffee and Muffin,Sandwich   
4                             Burgers,Pizza,Salads   
..                                             ...   
412                     Tacos,Quesadillas,Burritos   
413                     Tacos,Quesadillas,Burritos   
414                     Tacos,Quesadillas,Burritos   
415                     Tacos,Quesadillas,Burritos   
416                     Tacos,Quesadillas,Burritos   

                                      menu_items_array  
0             [Steakburgers, Milkshakes, French Fries]  
1    [Burger and Fries, Chicken Sandwich, Pizza Slice]  
2                            [Nachos, Tacos, Burritos]  
3     [Breakfast Burrito, Coffee and Muffin, Sandwich]  
4                             [Burgers, Pizza, Salads]  
..                                                 ...  
412                     [Tacos, Quesadillas, Burritos]  
413                     [Tacos, Quesadillas, Burritos]  
414                     [Tacos, Quesadillas, Burritos]  
415                     [Tacos, Quesadillas, Burritos]  
416                     [Tacos, Quesadillas, Burritos]  

[417 rows x 4 columns]

In [78]:
%%bigquery
with menu_items as (select name as business_name, split(menu_items, ',') as menu_items_array
                    from air_travel_int.Business
                    where dining = True)
select business_name, menu_item
from menu_items, unnest(menu_items_array) as menu_item

Query is running:   0%|          |

Downloading:   0%|          |

business_name                 menu_item
0     Applebee's Grill + Bar           Chicken Tenders
1     Applebee's Grill + Bar                     Steak
2     Applebee's Grill + Bar             Shrimp Scampi
3                Miami Grill              Miami Burger
4                Miami Grill  Grilled Chicken Sandwich
...                      ...                       ...
1246    The Peached Tortilla               Quesadillas
1247    The Peached Tortilla                  Burritos
1248             Tacos Locos                     Tacos
1249             Tacos Locos               Quesadillas
1250             Tacos Locos                  Burritos

[1251 rows x 2 columns]

##### Create the final table

In [79]:
%%bigquery
create or replace table air_travel_int.Menu_Items as
    with menu_items as (select name as business_name, split(menu_items, ',') as menu_items_array
                    from air_travel_int.Business
                    where dining = True)
    select business_name, menu_item
    from menu_items, unnest(menu_items_array) as menu_item

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [80]:
%%bigquery
select * from air_travel_int.Menu_Items
order by business_name

Query is running:   0%|          |

Downloading:   0%|          |

business_name      menu_item
0      12th Fairway Bar & Grill        Burgers
1      12th Fairway Bar & Grill     Sandwiches
2      12th Fairway Bar & Grill         Salads
3     13th Street Pub and Grill     Pub Burger
4     13th Street Pub and Grill  Chicken Wings
...                         ...            ...
1246                Zocalo Cafe       Burritos
1247                Zocalo Cafe    Quesadillas
1248                Zona Fresca          Tacos
1249                Zona Fresca       Burritos
1250                Zona Fresca    Quesadillas

[1251 rows x 2 columns]

##### Check for uniqueness of primary key fields

In [81]:
%%bigquery
select business_name, menu_item, count(*) as count
from air_travel_int.Menu_Items
group by business_name, menu_item
having count(*) > 1
order by business_name

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [business_name, menu_item, count]
Index: []

##### Remove the menu_items field from the `Business` table

In [82]:
%%bigquery
alter table air_travel_int.Business
    drop column menu_items

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [83]:
%%bigquery
select * from air_travel_int.Business

Query is running:   0%|          |

Downloading:   0%|          |

name    category  dining
0        Applebee's Grill + Bar      Dining    True
1                   Miami Grill      Dining    True
2         Cheeburger Cheeburger      Dining    True
3           Pints-Flights-Bites      Dining    True
4                    Torn Basil      Dining    True
..                          ...         ...     ...
778      Jose Cuervo Tequileria  Restaurant    True
779                    Loteria!  Restaurant    True
780  Earl Campbell's Taco Truck  Restaurant    True
781        The Peached Tortilla  Restaurant    True
782                 Tacos Locos  Restaurant    True

[783 rows x 3 columns]

In [85]:
%%bigquery
select * from air_travel_int.Menu_Items
order by business_name

Query is running:   0%|          |

Downloading:   0%|          |

business_name      menu_item
0      12th Fairway Bar & Grill        Burgers
1      12th Fairway Bar & Grill     Sandwiches
2      12th Fairway Bar & Grill         Salads
3     13th Street Pub and Grill     Pub Burger
4     13th Street Pub and Grill  Chicken Wings
...                         ...            ...
1246                Zocalo Cafe       Burritos
1247                Zocalo Cafe    Quesadillas
1248                Zona Fresca          Tacos
1249                Zona Fresca       Burritos
1250                Zona Fresca    Quesadillas

[1251 rows x 2 columns]

#### Create `Country`

In [ ]:
%%bigquery
select * from air_travel_stg.countries
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_code _data_source  \
0                  Afghanistan       AF         AF  openflights   
1                      Albania       AL         AL  openflights   
2                      Algeria       DZ         AG  openflights   
3               American Samoa       AS         AQ  openflights   
4                       Angola       AO         AO  openflights   
..                         ...      ...        ...          ...   
256  Wallis and Futuna Islands       WF         WF  openflights   
257             Western Sahara       EH         WI  openflights   
258                      Yemen       YE         YM  openflights   
259                     Zambia       ZM         ZA  openflights   
260                   Zimbabwe       ZW         ZI  openflights   

                          _load_time  
0   2024-08-25 16:07:35.067732+00:00  
1   2024-08-25 16:07:35.067732+00:00  
2   2024-08-25 16:07:35.067732+00:00  
3   2024-08-25 16:07:35.067732+00:00  
4   2024-08-25 16:07:35.067732+00:00  
..                               ...  
256 2024-08-25 16:07:35.067732+00:00  
257 2024-08-25 16:07:35.067732+00:00  
258 2024-08-25 16:07:35.067732+00:00  
259 2024-08-25 16:07:35.067732+00:00  
260 2024-08-25 16:07:35.067732+00:00  

[261 rows x 5 columns]

##### Check uniqueness of primary key field

In [ ]:
%%bigquery
select name, count(*) as count
from air_travel_stg.countries
group by name
having count(*) > 1
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name  count
0      India      2
1  Palestine      2

In [ ]:
%%bigquery
select * from air_travel_stg.countries
where name in ('India', 'Palestine')

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_code _data_source                       _load_time
0      India       IN         IN  openflights 2024-08-25 16:07:35.067732+00:00
1      India       IN         BS  openflights 2024-08-25 16:07:35.067732+00:00
2  Palestine       PS         WE  openflights 2024-08-25 16:07:35.067732+00:00
3  Palestine       PS         GZ  openflights 2024-08-25 16:07:35.067732+00:00

##### Turn `dafif_code` into an array type, so that we can get rid of the duplicate records for India and Palestine

In [ ]:
%%bigquery
select name, iso_code, array_agg(dafif_code) as dafif_codes
from air_travel_stg.countries
group by name, iso_code;

Executing query with job ID: 5a500043-107d-46d8-891b-7f59eb24701e
Query executing: 0.42s


ERROR:
 400 Array cannot have a null element; error in writing field dafif_codes; reason: invalidQuery, location: query, message: Array cannot have a null element; error in writing field dafif_codes

Location: us-central1
Job ID: 5a500043-107d-46d8-891b-7f59eb24701e



In [ ]:
%%bigquery
select name, iso_code, array_agg(ifnull(dafif_code, 'Unknown')) as dafif_codes
from air_travel_stg.countries
where name in ('India', 'Palestine') or dafif_code is null
group by name, iso_code;

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_codes
0  Bonaire, Saint Eustatius and Saba       BQ   [Unknown]
1                              India       IN    [IN, BS]
2                          Palestine       PS    [WE, GZ]

##### Create the final table

In [ ]:
%%bigquery
create or replace table air_travel_int.Country as
    select name, iso_code, array_agg(ifnull(dafif_code, 'Unknown')) as dafif_codes
    from air_travel_stg.countries
    group by name, iso_code;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key field

In [ ]:
%%bigquery
select name, count(*) as count
from air_travel_int.Country
group by name
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [name, count]
Index: []

#### `Airline` table

In [58]:
%%bigquery
select * from air_travel_stg.airlines
where country is not null

Query is running:   0%|          |

Downloading:   0%|          |

airline_id                         name alias  iata icao      callsign  \
0           3286    Linhas Aereas Santomenses  None  None  SMS   SANTOMENSES   
1           1390   British Gulf International  None  None  BGI  BRITISH GULF   
2           3208                        LASTP  None  None  OTN         LASTP   
3           3591            Natalco Air Lines  None  None  NCO       NATALCO   
4           2290  Express International Cargo  None  None  EIC       EXCARGO   
...          ...                          ...   ...   ...  ...           ...   
6139        2773           Hong Kong Airlines  None    HX  CRK      BAUHINIA   
6140        1680               Cathay Pacific  None    CX  CPA        CATHAY   
6141        3233                 Lao Airlines  None    QV  LAO           LAO   
6142       11724                      SVG Air  None  None  SVG    Grenadines   
6143         998                    Air Koryo  None    JS  KOR     AIR KORYO   

                                    country  active _data_source  \
0                                         S   False  openflights   
1                                         S   False  openflights   
2                                         S   False  openflights   
3                                         S   False  openflights   
4                                         S   False  openflights   
...                                     ...     ...          ...   
6139                 Hong Kong SAR of China    True  openflights   
6140                 Hong Kong SAR of China    True  openflights   
6141        Lao Peoples Democratic Republic    True  openflights   
6142       Saint Vincent and the Grenadines    True  openflights   
6143  Democratic People's Republic of Korea    True  openflights   

                           _load_time  
0    2024-08-25 15:52:55.956309+00:00  
1    2024-08-25 15:52:55.956309+00:00  
2    2024-08-25 15:52:55.956309+00:00  
3    2024-08-25 15:52:55.956309+00:00  
4    2024-08-25 15:52:55.956309+00:00  
...                               ...  
6139 2024-08-25 15:52:55.956309+00:00  
6140 2024-08-25 15:52:55.956309+00:00  
6141 2024-08-25 15:52:55.956309+00:00  
6142 2024-08-25 15:52:55.956309+00:00  
6143 2024-08-25 15:52:55.956309+00:00  

[6144 rows x 10 columns]

##### Look for any unmatched countries (as countries will be a FK on this table)

In [13]:
%%bigquery
select distinct name, country
from air_travel_stg.airlines
where country not in (select name from air_travel_int.Country)
order by country

Query is running:   0%|          |

Downloading:   0%|          |

name                country
0                    Sedalia   Boonville Stage Line
1                      Aires                   S.A.
2    Southern Jersey Airways                   ACOM
3        Active Aero Charter            ACTIVE AERO
4                 Aerocenter             AEROCENTER
..                       ...                    ...
210     Syrian Arab Airlines   Syrian Arab Republic
211   Empresa (Aero Uruguay)          UNIFORM OSCAR
212             RAF St Athan         UNited Kingdom
213                    Veles                  VELES
214  Ministry of Agriculture               WATCHDOG

[215 rows x 2 columns]

##### Look to see if we can use `soundex()` to find some more matches

In [12]:
%%bigquery
select a.id, a.name, a.country as airline_tbl_country, soundex(a.country) as airline_tbl_soundex, c.name as country_table_country, soundex(c.name) as country_table_soundex, a.active
from air_travel_stg.airlines a, air_travel_int.Country c
where soundex(a.country) = soundex(c.name)

Query is running:   0%|          |

Downloading:   0%|          |

id                                     name     airline_tbl_country  \
0       3207  LAP Colombia - Lineas Aereas Petroleras                     LAP   
1       1312                              Air Horizon                    Chad   
2        433                                Air Tchad                    Chad   
3       4942                         Toumai Air Tchad                    Chad   
4        894                       Air Affaires Tchad                    Chad   
...      ...                                      ...                     ...   
11356  16844                              BVI Airways  British Virgin Islands   
11357  16844                              BVI Airways  British Virgin Islands   
11358   1680                           Cathay Pacific  Hong Kong SAR of China   
11359   2773                       Hong Kong Airlines  Hong Kong SAR of China   
11360   2774                Hong Kong Express Airways  Hong Kong SAR of China   

      airline_tbl_soundex           country_table_country  \
0                    L100                           Libya   
1                    C300                            Chad   
2                    C300                            Chad   
3                    C300                            Chad   
4                    C300                            Chad   
...                   ...                             ...   
11356                B632  British Indian Ocean Territory   
11357                B632          British Virgin Islands   
11358                H525                       Hong Kong   
11359                H525                       Hong Kong   
11360                H525                       Hong Kong   

      country_table_soundex  active  
0                      L100   False  
1                      C300   False  
2                      C300   False  
3                      C300   False  
4                      C300   False  
...                     ...     ...  
11356                  B632    True  
11357                  B632    True  
11358                  H525    True  
11359                  H525    True  
11360                  H525    True  

[11361 rows x 7 columns]

##### Don't use soundex due to false positives (e.g. LAP should be in Columbia, not Lybia)

##### Use the LLM to look for matches

In [15]:
import vertexai
from vertexai.generative_models import GenerativeModel, Part

project_id = "cs378-fa2024"
region = "us-central1"
model_name = "gemini-1.5-flash-001"
prompt = """Find a match for each country based on the master list of 4 countries below.
For example, if I pass you the country 'Syrian Arab Republic', map it to the country 'Syria'.
If there is no good match, return the original country and null.
Don't match to any countries which are not on the master list.
Format your answer as a list of json objects, with the schema: [{current:string, new:string}].

Below is the master list of countries (to match against):
Switzerland
Sri Lanka
South Africa
Syria
"""

unmatched = "Swaziland, Syrian Arab Republic, S.A., WATCHDOG"

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)
resp = model.generate_content([unmatched, prompt])
resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
print(resp_text)

[  {    "current": "Swaziland",    "new": "null"  },  {    "current": "Syrian Arab Republic",    "new": "Syria"  },  {    "current": "S.A.",    "new": "South Africa"  },  {    "current": "WATCHDOG",    "new": "null"  }]


##### Refine prompt and run on entire list of unmatched countries

In [107]:
import vertexai
from vertexai.generative_models import GenerativeModel, Part

project_id = "cs378-fa2024"
region = "us-central1"
model_name = "gemini-1.5-flash-001"
prompt = """Find a match for each country based on the list of 256 countries below.
For example, if I pass you the country 'Syrian Arab Republic', map it to 'Syria'.
If there is no good match, default to null
Format your answer as a dictionary, with the schema: {current<string>: new<string>}.
For example, {"Syrian Arab Republic": "Syria", "Swaziland": null}
Below are the list of countries you should match against:
"""

bq_client = bigquery.Client()
prompt_sql = "select name from air_travel_int.Country"
rows = bq_client.query_and_wait(prompt_sql)
prompt_countries = ""

for row in rows:
    prompt_countries += f"{row['name']}, "

prompt = prompt + prompt_countries[:-2]  # lose the last comma
print("prompt:", prompt)

umatched_countries = """select distinct country from air_travel_stg.airlines
where country not in (select name from air_travel_int.Country)
"""

input_str = ""

rows = bq_client.query_and_wait(umatched_countries)

for row in rows:
    input_str += f"{row['country']}, "
input_str = input_str[:-2] # lose the last comma

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)
resp = model.generate_content([input_str, prompt])
resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
print("results_raw:", resp_text)
replacements = json.loads(resp_text)
print("replacements:", replacements)

# load dataframe and merge results
airline_table = """
select * except (_data_source, _load_time)
from air_travel_stg.airlines
where country is not null
and country not in (select name from air_travel_int.Country)
order by country
"""

df = bq_client.query_and_wait(airline_table).to_dataframe()
#print("orig df:", df.to_string())

df["country"] = df["country"].map(replacements)
#print("new df:", df.to_string())

table_id = "air_travel_int.tmp_airlines_countries_filtered"
pandas_gbq.to_gbq(df, table_id, project_id=project_id, if_exists="replace")

prompt: Find a match for each country based on the list of 256 countries below.
For example, if I pass you the name 'Syrian Arab Republic', map it to the country Syria.
If there is no good match, default to null
Format your answer as a dictionary, with the schema: {current<string>: new<string>}.
For example, {"Syrian Arab Republic": "Syria", "Swaziland": null}
Below are the list of countries you should match against:
Ashmore and Cartier Islands, Baker Island, Howland Island, Kingman Reef, Tromelin Island, Clipperton Island, Midway Islands, Europa Island, Jan Mayen, Spratly Islands, Johnston Atoll, Wake Island, Juan de Nova Island, Paracel Islands, Palmyra Atoll, Jarvis Island, Glorioso Islands, Navassa Island, Coral Sea Islands, United Arab Emirates, Afghanistan, Antigua and Barbuda, Anguilla, Albania, Armenia, Netherlands Antilles, Angola, Antarctica, Argentina, American Samoa, Austria, Australia, Aruba, Azerbaijan, Bosnia and Herzegovina, Barbados, Bangladesh, Belgium, Burkina Faso, 

100%|██████████| 1/1 [00:00<00:00, 7332.70it/s]


In [109]:
%%bigquery
select * from air_travel_int.tmp_airlines_countries_filtered
where country is not null
order by country

Query is running:   0%|          |

Downloading:   0%|          |

id                    name alias  iata icao     callsign  \
0     4255   Royal Brunei Airlines  None    BI  RBA       BRUNEI   
1     1601      Cabo Verde Express  None  None  CVE        KABEX   
2     2873  Inter Islands Airlines  None    H4  IIN         None   
3    11804              Halcyonair  None    7Z   \N       CREOLE   
4    18762              Lina Congo  None    GC   \N         None   
..     ...                     ...   ...   ...  ...          ...   
144   3808              Orient Air  None  None  OVV    ORIENTSYR   
145   1574      C Air Jet Airlines  None  None  SRJ       SYRJET   
146   1975       Damascene Airways  None  None  DAS       AIRDAM   
147   4586    Syrian Arab Airlines  None    RB  SYR    SYRIANAIR   
148   4121            RAF St Athan  None  None  STN  SAINT ATHAN   

               country  active  
0    Brunei Darussalam    True  
1           Cabo Verde   False  
2           Cabo Verde   False  
3           Cabo Verde    True  
4       Congo Republic   False  
..                 ...     ...  
144              Syria   False  
145              Syria   False  
146              Syria   False  
147              Syria    True  
148     United Kingdom   False  

[149 rows x 8 columns]

##### Create the final table, reordering the fields

In [21]:
%%bigquery
select id, name, alias, icao, iata, callsign, country, active
from air_travel_stg.airlines
where country in (select name from air_travel_int.Country)
union distinct
select id, name, alias, icao, iata, callsign, country, active
from air_travel_int.tmp_airlines_countries_filtered
where country is not null
order by country

Query is running:   0%|          |

Downloading:   0%|          |

id                         name                   alias icao  iata  \
0      3138       Khyber Afghan Airlines                    None  KHY  None   
1      3402            Marcopolo Airways                    None  MCP  None   
2      1397               Balkh Airlines                    None  BHI  None   
3      3878                Pamir Airways                    None  PIR    NR   
4     18672                 East Horizon                    None  EHN  None   
...     ...                          ...                     ...  ...   ...   
6072   3446  Medical Air Rescue Services                    None  MRZ  None   
6073   1266              Avient Aviation                    None  SMJ    Z3   
6074    608                 Air Zimbabwe                    None  AZW    UM   
6075  20051          Fly Africa Zimbabwe  Zimbabwe flyafrica.com  FZW  None   
6076   5210          United Air Charters                    None  UAC  None   

           callsign      country  active  
0            KHYBER  Afghanistan   False  
1         MARCOPOLO  Afghanistan   False  
2            SHARIF  Afghanistan   False  
3             PAMIR  Afghanistan   False  
4      EAST HORIZON  Afghanistan    True  
...             ...          ...     ...  
6072           MARS     Zimbabwe   False  
6073         AVAVIA     Zimbabwe    True  
6074   AIR ZIMBABWE     Zimbabwe    True  
6075  Fresh Express     Zimbabwe    True  
6076        UNITAIR     Zimbabwe    True  

[6077 rows x 8 columns]

In [113]:
%%bigquery
create or replace table air_travel_int.Airline as
    select * except (_data_source, _load_time)
    from air_travel_stg.airlines
    where country in (select name from air_travel_int.Country)
    union distinct
    select *
    from air_travel_int.tmp_airlines_countries_filtered
    where country is not null
    order by country

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check primary key uniqueness

In [22]:
%%bigquery
select id, count(*) as count
from air_travel_int.Airline
group by id
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [id, count]
Index: []

##### Clean up

In [94]:
%%bigquery
drop table if exists air_travel_int.tmp_airlines_countries_filtered

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### `Aircraft` table

In [30]:
%%bigquery
select * from air_travel_stg.aircrafts
where icao is null or iata is null
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name  iata  icao _data_source  \
0                        Airbus A330   330  None  openflights   
1          Airbus A330-700 Beluga XL  None  A337  openflights   
2                        Airbus A340   340  None  openflights   
3                        Airbus A350   350  None  openflights   
4                        Airbus A380   380  None  openflights   
5                            BAe 146   146  None  openflights   
6                   Beechcraft Baron  None  BE58  openflights   
7        Beechcraft Baron / 55 Baron  None  BE55  openflights   
8                         Boeing 727   727  None  openflights   
9                         Boeing 737   737  None  openflights   
10                 Boeing 737 MAX 10   7MJ  None  openflights   
11                        Boeing 747   747  None  openflights   
12                        Boeing 757   757  None  openflights   
13                        Boeing 767   767  None  openflights   
14                        Boeing 777   777  None  openflights   
15                        Boeing 787   787  None  openflights   
16                    Bombardier 415  None  CL2T  openflights   
17  Bombardier BD-100 Challenger 300  None  CL30  openflights   
18                       COMAC C-919  None  C919  openflights   
19                        Cessna 152  None  C152  openflights   
20                       Embraer 175   E75  None  openflights   
21                Embraer Legacy 450  None  E545  openflights   
22        Piper PA-28 (above 200 hp)  None  P28B  openflights   
23        Piper PA-28 (up to 180 hp)  None  P28A  openflights   
24              Piper PA-44 Seminole  None  PA44  openflights   
25                    Tupolev Tu-144  None  T144  openflights   

                         _load_time  
0  2024-08-25 16:15:09.744963+00:00  
1  2024-08-25 16:15:09.744963+00:00  
2  2024-08-25 16:15:09.744963+00:00  
3  2024-08-25 16:15:09.744963+00:00  
4  2024-08-25 16:15:09.744963+00:00  
5  2024-08-25 16:15:09.744963+00:00  
6  2024-08-25 16:15:09.744963+00:00  
7  2024-08-25 16:15:09.744963+00:00  
8  2024-08-25 16:15:09.744963+00:00  
9  2024-08-25 16:15:09.744963+00:00  
10 2024-08-25 16:15:09.744963+00:00  
11 2024-08-25 16:15:09.744963+00:00  
12 2024-08-25 16:15:09.744963+00:00  
13 2024-08-25 16:15:09.744963+00:00  
14 2024-08-25 16:15:09.744963+00:00  
15 2024-08-25 16:15:09.744963+00:00  
16 2024-08-25 16:15:09.744963+00:00  
17 2024-08-25 16:15:09.744963+00:00  
18 2024-08-25 16:15:09.744963+00:00  
19 2024-08-25 16:15:09.744963+00:00  
20 2024-08-25 16:15:09.744963+00:00  
21 2024-08-25 16:15:09.744963+00:00  
22 2024-08-25 16:15:09.744963+00:00  
23 2024-08-25 16:15:09.744963+00:00  
24 2024-08-25 16:15:09.744963+00:00  
25 2024-08-25 16:15:09.744963+00:00

##### Look up the missing icao and iata codes with LLM

In [31]:
import json
import pandas, pandas_gbq
from google.cloud import bigquery
import vertexai
from vertexai.generative_models import GenerativeModel, Part

project_id = "cs378-fa2024"
region = "us-central1"
model_name = "gemini-1.5-flash-001"
prompt = """For each aircraft, provide the icao and iata codes that best its description.
For example, if I give you the aircraft 'Boeing 737', return the icao code 'B737' and the iata code '73G'.
If you can't find either code, return null.
Format your answer as a list of dictionaries, with the schema: {name<string>, icao<string>, iata<string>}.
For example, {"name": "Boeing 737", "icao": "B737", "iata": "73G"}
"""

bq_client = bigquery.Client()

input_sql = """select name from air_travel_stg.aircrafts
where icao is null or iata is null
"""

input_str = ""

rows = bq_client.query_and_wait(input_sql)

for row in rows:
    input_str += f"{row['name']}, "
input_str = input_str[:-2] # lose the last comma

vertexai.init(project=project_id, location=region)
model = GenerativeModel(model_name)
resp = model.generate_content([input_str, prompt])
resp_text = resp.text.replace("```json", "").replace("```", "").replace("\n", "")
print("results_raw:", resp_text)
replacements = json.loads(resp_text)
print("replacements:", replacements)

df = pandas.DataFrame(replacements)
print("df:", df.to_string())

table_id = "air_travel_int.tmp_aircrafts"
pandas_gbq.to_gbq(df, table_id, project_id=project_id, if_exists="replace")

results_raw: [  {"name": "Boeing 767", "icao": "B767", "iata": "76W"},  {"name": "Boeing 747", "icao": "B747", "iata": "74R"},  {"name": "Airbus A340", "icao": "A340", "iata": "34Q"},  {"name": "Boeing 777", "icao": "B777", "iata": "77W"},  {"name": "Airbus A380", "icao": "A380", "iata": "38W"},  {"name": "Boeing 727", "icao": "B727", "iata": "72G"},  {"name": "Embraer 175", "icao": "E175", "iata": "175"},  {"name": "Airbus A350", "icao": "A350", "iata": "35K"},  {"name": "Boeing 737", "icao": "B737", "iata": "73G"},  {"name": "BAe 146", "icao": "BAE146", "iata": "146"},  {"name": "Boeing 737 MAX 10", "icao": "B73M", "iata": "73M"},  {"name": "Airbus A330", "icao": "A330", "iata": "33Q"},  {"name": "Boeing 757", "icao": "B757", "iata": "75W"},  {"name": "Boeing 787", "icao": "B787", "iata": "78W"},  {"name": "Airbus A330-700 Beluga XL", "icao": "A338", "iata": "338"},  {"name": "Beechcraft Baron / 55 Baron", "icao": "BE58", "iata": null},  {"name": "Beechcraft Baron", "icao": "BE58", "

100%|██████████| 1/1 [00:00<00:00, 7653.84it/s]


In [32]:
%%bigquery
select * from air_travel_int.tmp_aircrafts

Query is running:   0%|          |

Downloading:   0%|          |

name    icao  iata
0        Beechcraft Baron / 55 Baron    BE58  None
1                   Beechcraft Baron    BE58  None
2                         Cessna 152    C152  None
3                     Bombardier 415   CL415  None
4   Bombardier BD-100 Challenger 300   CL300  None
5                 Embraer Legacy 450   LE450  None
6         Piper PA-28 (up to 180 hp)    PA28  None
7         Piper PA-28 (above 200 hp)    PA28  None
8               Piper PA-44 Seminole    PA44  None
9                     Tupolev Tu-144   TU144  None
10                           BAe 146  BAE146   146
11                       Embraer 175    E175   175
12         Airbus A330-700 Beluga XL    A338   338
13                       Airbus A330    A330   33Q
14                       Airbus A340    A340   34Q
15                       Airbus A350    A350   35K
16                       Airbus A380    A380   38W
17                        Boeing 727    B727   72G
18                        Boeing 737    B737   73G
19                 Boeing 737 MAX 10    B73M   73M
20                        Boeing 747    B747   74R
21                        Boeing 757    B757   75W
22                        Boeing 767    B767   76W
23                        Boeing 777    B777   77W
24                        Boeing 787    B787   78W
25                       COMAC C-919    C919   919

##### Merge results into new temp table

In [33]:
%%bigquery
create or replace table air_travel_int.tmp_aircrafts_merged as
    select icao, iata, name
    from air_travel_stg.aircrafts

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [34]:
%%bigquery
update air_travel_int.tmp_aircrafts_merged m
    set icao = (select icao from air_travel_int.tmp_aircrafts t where t.name = m.name)
    where icao is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [35]:
%%bigquery
update air_travel_int.tmp_aircrafts_merged m
    set iata = (select iata from air_travel_int.tmp_aircrafts t where t.name = m.name)
    where iata is null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [36]:
%%bigquery
select * from air_travel_int.tmp_aircrafts_merged
where icao is null

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [icao, iata, name]
Index: []

##### Check uniqueness of primary key field

In [37]:
%%bigquery
select icao, count(*) as count
from air_travel_int.tmp_aircrafts_merged
group by icao
having count(*) > 1

Query is running:   0%|          |

Downloading:   0%|          |

icao  count
0  B737      2
1  E135      2

In [38]:
%%bigquery
select * from air_travel_int.tmp_aircrafts_merged
where icao in ('B737', 'E135')
order by icao

Query is running:   0%|          |

Downloading:   0%|          |

icao iata            name
0  B737  737      Boeing 737
1  B737  73G  Boeing 737-700
2  E135  ER3   Embraer RJ135
3  E135  ERD   Embraer RJ140

##### Manually remove the two duplicate records

In [39]:
%%bigquery
delete from air_travel_int.tmp_aircrafts_merged
    where icao = 'B737' and iata = '737';
delete from air_travel_int.tmp_aircrafts_merged
    where icao = 'E135' and iata = 'ERD';

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Create the final table with icao being the primary key

In [40]:
%%bigquery
create or replace table air_travel_int.Aircraft as
    select icao, iata, name
    from air_travel_int.tmp_aircrafts_merged
    where icao is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Clean up

In [129]:
%%bigquery
drop table if exists air_travel_int.tmp_aircrafts;
drop table if exists air_travel_int.tmp_aircrafts_merged;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### `Flight_Routes` table (anomaly type 9)

In [2]:
%%bigquery
select * from air_travel_stg.flight_routes
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

airline_code airline_id source_airport source_airport_id dest_airport  \
0           2B        410            DME              4029          TGK   
1           2G       1654            IKT              2937          KCK   
2           4O      17885            MEX              1824          PQM   
3           5Z      18946            CPT               797          PBZ   
4           6E       2850            PNQ              3017          HYD   
5           6E       2850            VTZ              3066          HYD   
6           6E       2850            BLR              3131          HYD   
7           6E       2850            CCU              3043          HYD   
8           6E       2850            AMD              2994          HYD   
9           6E       2850            BOM              2997          HYD   

  dest_airport_id  codeshare  stops equipment _data_source  \
0            None       <NA>      0       CR2  openflights   
1            None       <NA>      0       AN4  openflights   
2            None       <NA>      0       SU9  openflights   
3            None       <NA>      0       BEH  openflights   
4            None       <NA>      0       320  openflights   
5            None       <NA>      0       320  openflights   
6            None       <NA>      0       320  openflights   
7            None       <NA>      0       320  openflights   
8            None       <NA>      0       320  openflights   
9            None       <NA>      0       320  openflights   

                        _load_time  
0 2024-08-25 16:19:41.311112+00:00  
1 2024-08-25 16:19:41.311112+00:00  
2 2024-08-25 16:19:41.311112+00:00  
3 2024-08-25 16:19:41.311112+00:00  
4 2024-08-25 16:19:41.311112+00:00  
5 2024-08-25 16:19:41.311112+00:00  
6 2024-08-25 16:19:41.311112+00:00  
7 2024-08-25 16:19:41.311112+00:00  
8 2024-08-25 16:19:41.311112+00:00  
9 2024-08-25 16:19:41.311112+00:00

##### See if we have any unmatched airlines which are present in the staging table

In [16]:
%%bigquery
select * from air_travel_stg.airlines
where id in
    (select distinct airline_id
    from air_travel_stg.flight_routes
    where airline_id not in (select id from air_travel_int.Airline))
order by id

Query is running:   0%|          |

Downloading:   0%|          |

id                                       name alias iata  icao  \
0    68                                  Air Tindi  None   8T  None   
1   439                            Alaska Airlines  None   AS   ASA   
2   515  Avianca - Aerovias Nacionales de Colombia  None   AV   AVA   
3  2056                                  Dragonair  None   KA   HDA   

                     callsign               country  active _data_source  \
0                        None  Canadian Territories    True  openflights   
1                        Inc.                ALASKA    True  openflights   
2                        S.A.               AVIANCA    True  openflights   
3   Hong Kong Dragon Airlines                DRAGON    True  openflights   

                        _load_time  
0 2024-08-25 15:52:55.956309+00:00  
1 2024-08-25 15:52:55.956309+00:00  
2 2024-08-25 15:52:55.956309+00:00  
3 2024-08-25 15:52:55.956309+00:00

##### Add the missing airline records from staging and update their country names by hand so that we can keep the unmatched flight routes

In [20]:
%%bigquery
select * from air_travel_int.Country
where name in ('Canada', 'United States', 'Colombia', 'Hong Kong')
order by name

Query is running:   0%|          |

Downloading:   0%|          |

name iso_code dafif_codes
0         Canada       CA        [CA]
1       Colombia       CO        [CO]
2      Hong Kong       HK        [HK]
3  United States       US        [US]

In [23]:
%%bigquery
insert into air_travel_int.Airline (id, name, alias, icao, iata, callsign, country, active)
    select id, name, alias, icao, iata, callsign, country, active
    from air_travel_stg.airlines
    where country in ('Canadian Territories', 'ALASKA', 'AVIANCA', 'DRAGON')

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [24]:
%%bigquery
update air_travel_int.Airline set country = 'Canada'
    where country = 'Canadian Territories';
update air_travel_int.Airline set country = 'United States'
    where country = 'ALASKA';
update air_travel_int.Airline set country = 'Colombia'
    where country = 'AVIANCA';
update air_travel_int.Airline set country = 'Hong Kong'
    where country = 'DRAGON';

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [25]:
%%bigquery
select * from air_travel_int.Airline
where id in (68, 439, 515, 2056)

Query is running:   0%|          |

Downloading:   0%|          |

id                                       name alias iata  icao  \
0  2056                                  Dragonair  None   KA   HDA   
1    68                                  Air Tindi  None   8T  None   
2   515  Avianca - Aerovias Nacionales de Colombia  None   AV   AVA   
3   439                            Alaska Airlines  None   AS   ASA   

                     callsign        country  active  
0   Hong Kong Dragon Airlines      Hong Kong    True  
1                        None         Canada    True  
2                        S.A.       Colombia    True  
3                        Inc.  United States    True

##### Confirm that we have no more unmatched airlines

In [26]:
%%bigquery
select * from air_travel_stg.flight_routes
where airline_id not in (select id from air_travel_int.Airline)

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airline_code, airline_id, source_airport, source_airport_id, dest_airport, dest_airport_id, codeshare, stops, equipment, _data_source, _load_time]
Index: []

##### Look up the icao code for both the source and destination airports, replacing airport_id with icao codes (anomaly type 9). Don't exclude any routes which have missing icao codes

In [40]:
%%bigquery
select f.airline_id, a1.icao as source_airport_icao, f.source_airport as source_airport_iata,
    a2.icao as dest_airport_icao, f.dest_airport as dest_airport_iata,
    f.codeshare, f.stops, f.equipment
from air_travel_stg.flight_routes f join air_travel_stg.airports a1
on f.source_airport_id = a1.airport_id
join air_travel_stg.airports a2 on f.dest_airport_id = a2.airport_id

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao source_airport_iata dest_airport_icao  \
0            1203                LFBZ                 BIQ              LFQQ   
1            1203                LFBZ                 BIQ              LFMN   
2            1203                LFBZ                 BIQ              LFLL   
3            1203                LFBZ                 BIQ              LSGG   
4             137                LFBZ                 BIQ              LFPO   
...           ...                 ...                 ...               ...   
67235        1758                ZULZ                 LZO              ZSHC   
67236        1758                ZULZ                 LZO              ZPPP   
67237        1758                ZULZ                 LZO              ZBAA   
67238        4611                ZULZ                 LZO              ZGGG   
67239         146                None                 AOS              None   

      dest_airport_iata  codeshare  stops        equipment  
0                   LIL       <NA>      0              ER4  
1                   NCE       <NA>      0              CR7  
2                   LYS       <NA>      0          CR7 ER4  
3                   GVA       <NA>      0              CR7  
4                   ORY       <NA>      0  CRK 319 321 320  
...                 ...        ...    ...              ...  
67235               HGH       <NA>      0              737  
67236               KMG       <NA>      0              737  
67237               PEK       <NA>      0          737 319  
67238               CAN       True      0              737  
67239               KZB       <NA>      0              BNI  

[67240 rows x 8 columns]

##### Materialize results as tmp table

In [86]:
%%bigquery
create or replace table air_travel_int.tmp_flight_routes as
    select f.airline_id, a1.icao as source_airport_icao, f.source_airport as source_airport_iata,
        a2.icao as dest_airport_icao, f.dest_airport as dest_airport_iata,
        f.codeshare, f.stops, f.equipment
    from air_travel_stg.flight_routes f join air_travel_stg.airports a1
    on f.source_airport_id = a1.airport_id
    join air_travel_stg.airports a2 on f.dest_airport_id = a2.airport_id

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Look for records which are missing icao codes

In [87]:
%%bigquery
select *
from air_travel_int.tmp_flight_routes
where source_airport_icao is null
or dest_airport_icao is null

Query is running:   0%|          |

Downloading:   0%|          |

airline_id source_airport_icao source_airport_iata dest_airport_icao  \
0          3498                None                 INB              None   
1         20963                None                 KPB              None   
2           146                None                 KKB              None   
3          1266                None                 HYL              None   
4          3498                None                 PLJ              None   
..          ...                 ...                 ...               ...   
390        2193                None                 JGS              ZUUU   
391         751                None                 NTG              ZYTL   
392        4611                None                 NTG              ZYTL   
393        4611                None                 NTG              ZYTX   
394         751                None                 NTG              ZYTX   

    dest_airport_iata  codeshare  stops equipment  
0                 PND       <NA>      0       CNC  
1                 PPV       <NA>      0       DHP  
2                 SYB       <NA>      0       BNI  
3                 KTB       <NA>      0       DHP  
4                 PND       <NA>      0       CNC  
..                ...        ...    ...       ...  
390               CTU       <NA>      0       319  
391               DLC       True      0       738  
392               DLC       <NA>      0       738  
393               SHE       <NA>      0       738  
394               SHE       True      0       738  

[395 rows x 8 columns]

##### Look to see if the iata codes match up to unique records in the Airport table, so that we can determine if they can be used to fill in the missing icao codes

In [88]:
%%bigquery
select iata, count(*) as count
from air_travel_int.Airport
where iata in (select source_airport_iata from air_travel_int.tmp_flight_routes
               where source_airport_icao is null)
group by iata
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [iata, count]
Index: []

In [89]:
%%bigquery
select iata, count(*) as count
from air_travel_int.Airport
where iata in (select dest_airport_iata from air_travel_int.tmp_flight_routes
               where dest_airport_icao is null)
group by iata
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [iata, count]
Index: []

##### Given that all the iata codes are unique, we can use the iata to look up the missing icao codes

In [90]:
%%bigquery
select *
from air_travel_int.Airport
where iata in (select source_airport_iata from air_travel_int.tmp_flight_routes
               where source_airport_icao is null)
or iata in (select dest_airport_iata from air_travel_int.tmp_flight_routes
            where dest_airport_icao is null)

Query is running:   0%|          |

Downloading:   0%|          |

icao iata                  name  city state country  \
0  ZSJA  JGS  Jinggangshan Airport  Jian  None   China   

                                    latitude  \
0  26.85689926149999700000000000000000000000   

                                    longitude  altitude  timezone_name  \
0  114.73699951200000000000000000000000000000       281  Asia/Shanghai   

   timezone_delta daylight_savings_time     type       source  
0               8                     U  airport  OurAirports

In [91]:
%%bigquery
update air_travel_int.tmp_flight_routes
    set source_airport_icao = 'ZSJA' where source_airport_iata = 'JGS'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Look to see which equipment codes are present in the parent `Aircraft` table

In [92]:
%%bigquery
select distinct equipment
from air_travel_int.tmp_flight_routes
where equipment in (select iata from air_travel_int.Aircraft)

Query is running:   0%|          |

Downloading:   0%|          |

equipment
0         DHP
1         BNI
2         DHT
3         BH2
4         320
..        ...
108       A40
109       A81
110       TU5
111       T20
112       YK4

[113 rows x 1 columns]

##### How many equipment codes are not present?

In [1]:
%%bigquery
select distinct equipment
from air_travel_int.tmp_flight_routes
where equipment not in (select iata from air_travel_int.Aircraft)
order by length(equipment) desc

Query is running:   0%|          |

Downloading:   0%|          |

equipment
0     320 319 CR9 321 717 73G 73W 738 736
1     319 320 CR9 321 717 73G 73W 738 736
2     M90 M88 320 753 757 73H 777 319 738
3     320 738 330 319 739 321 343 73W 77W
4     321 320 333 772 773 777 744 E70 74E
...                                   ...
3822                                  M1F
3823                                  DC9
3824                                  MA6
3825                                  32C
3826                                  YN7

[3827 rows x 1 columns]

##### Note: there can be more than one aircraft type per flight route (e.g. 330, 738, 321, 320). We will decompose this relationship into its own table so that we can easily query it with SQL. This resolve anomaly type 8.

In [135]:
%%bigquery
select * from air_travel_int.Aircraft
where iata in ('319', '320', '321', '73G', '752', 'E90', '73H')

Query is running:   0%|          |

Downloading:   0%|          |

name  icao iata
0     Airbus A319  A319  319
1     Airbus A320  A320  320
2     Airbus A321  A321  321
3  Boeing 737-700  B737  73G
4  Boeing 757-200  B752  752
5     Embraer 190  E190  E90

##### Assign a new PK to the flight routes table, so that we can have a single field to uniquely identify each route. Split off the route id and equipment into a junction table to model the many-to-many.

In [8]:
%%bigquery
select row_number() over () as route_id,
    airline_id, source_airport_icao, dest_airport_icao, codeshare, stops, equipment
    from air_travel_int.tmp_flight_routes
    where airline_id is not null
    and source_airport_icao is not null
    and dest_airport_icao is not null

Query is running:   0%|          |

Downloading:   0%|          |

route_id  airline_id source_airport_icao dest_airport_icao  codeshare  \
0             1        2607                KDEN               EAR       <NA>   
1             2        2607                KLAX               IGM       <NA>   
2             3        2468                KLAX               IGM       True   
3             4        5209                KLAX               IGM       True   
4             5        2607                KPGA               IGM       <NA>   
...         ...         ...                 ...               ...        ...   
66394     66395         751                ZSQD              ZYYJ       True   
66395     66396        4599                ZSQD              ZYYJ       <NA>   
66396     66397        1758                ZSQD              ZYYJ       <NA>   
66397     66398        1767                ZYCC              ZYYJ       <NA>   
66398     66399        1767                ZYTL              ZYYJ       <NA>   

       stops equipment  
0          0       EM2  
1          0       BE1  
2          0       BE1  
3          0       BE1  
4          0       BE1  
...      ...       ...  
66394      0       737  
66395      0       737  
66396      0       320  
66397      0   320 321  
66398      0       319  

[66399 rows x 7 columns]

##### Materialize results to temp table, while excluding the records which are missing one of the primary key fields

In [93]:
%%bigquery
create or replace table air_travel_int.tmp_flight_routes_id as
    select row_number() over () as route_id,
    airline_id, source_airport_icao, dest_airport_icao, codeshare, stops, equipment
    from air_travel_int.tmp_flight_routes
    where airline_id is not null
    and source_airport_icao is not null
    and dest_airport_icao is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [45]:
%%bigquery
select * from air_travel_int.tmp_flight_routes_id

Query is running:   0%|          |

Downloading:   0%|          |

route_id  airline_id source_airport_icao dest_airport_icao  codeshare  \
0           137        1308                AYMD              AYNZ       <NA>   
1           145         328                AYCH              AYPY       <NA>   
2           168        1308                AYTB              AYPY       <NA>   
3           200         328                AYHK              AYTK       <NA>   
4           228         921                BGSC              BGCO       <NA>   
...         ...         ...                 ...               ...        ...   
66394     66206         751                ZSJN              ZYTL       True   
66395     66228       15999                ZSPD              ZYTL       <NA>   
66396     66278        1758                ZBAA              ZYTX       True   
66397     66280         690                ZBCF              ZYTX       <NA>   
66398     66298         751                ZGGG              ZYTX       True   

       stops equipment  
0          0       DH8  
1          0       DH8  
2          0       DH8  
3          0       DH4  
4          0       NDE  
...      ...       ...  
66394      0       CR2  
66395      0       320  
66396      0   321 320  
66397      0       ERJ  
66398      0       320  

[66399 rows x 7 columns]

##### Yes, technically we shifted the primary key to `route_id`, but the natural key is still {`airline_id`, `source_airport_icao`, `dest_airport_icao`}, so we should ensure uniqueness of those fields

In [46]:
%%bigquery
select airline_id, source_airport_icao, dest_airport_icao, count(*) as count
from air_travel_int.tmp_flight_routes_id
group by airline_id, source_airport_icao, dest_airport_icao
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airline_id, source_airport_icao, dest_airport_icao, count]
Index: []

##### Create a new junction table, `Route_Equipment`, to model the many-to-many between `Flight_Routes` and `Aircraft` (i.e. a route can have multiple equipment types and an equipment type can be used by multiple routes). We will create the final table for `Flight_Routes` after creating the junction table.

In [47]:
%%bigquery
select route_id, split(equipment, ' ') as equipment_array from air_travel_int.tmp_flight_routes_id

Query is running:   0%|          |

Downloading:   0%|          |

route_id equipment_array
0           228           [NDE]
1           252           [BH2]
2           317           [75W]
3           380           [AT4]
4           499           [AT4]
...         ...             ...
66394     42757           [SF3]
66395     42771           [SF3]
66396     49125           [SF3]
66397     57456           [SF3]
66398     57655           [SF3]

[66399 rows x 2 columns]

##### Materialize to temp table

In [94]:
%%bigquery
create or replace table air_travel_int.tmp_route_equipment as
    select route_id, split(equipment, ' ') as equipment_array
    from air_travel_int.tmp_flight_routes_id
    where equipment is not null

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [49]:
%%bigquery
select * from air_travel_int.tmp_route_equipment

Query is running:   0%|          |

Downloading:   0%|          |

route_id    equipment_array
0         18716  [, 73W, 733, 73C]
1         14500            [, 777]
2         33682              [100]
3         57808              [100]
4         40209              [100]
...         ...                ...
66378     66049              [YN7]
66379     66102              [YN7]
66380     66101              [YN7]
66381     59984              [YN7]
66382     66060              [YN7]

[66383 rows x 2 columns]

In [50]:
%%bigquery
select route_id, equipment
from air_travel_int.tmp_route_equipment cross join unnest(equipment_array) as equipment
where equipment != ''

Query is running:   0%|          |

Downloading:   0%|          |

route_id equipment
0         18716       73W
1         18716       733
2         18716       73C
3         14500       777
4         33682       100
...         ...       ...
91821     66049       YN7
91822     66102       YN7
91823     66101       YN7
91824     59984       YN7
91825     66060       YN7

[91826 rows x 2 columns]

##### Materialize unnested results to temp table

In [95]:
%%bigquery
create or replace table air_travel_int.tmp_route_equipment_unnested as
    select route_id, equipment
    from air_travel_int.tmp_route_equipment cross join unnest(equipment_array) as equipment
    where equipment != ''

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Join with the parent table, `Aircraft`, and replace the current iata code with the icao code (anomaly type 9)

In [42]:
%%bigquery
select re.*, a.*
from air_travel_int.tmp_route_equipment_unnested re join air_travel_int.Aircraft a
on a.iata = re.equipment

Query is running:   0%|          |

Downloading:   0%|          |

route_id equipment  icao iata                     name
0         40391       M82  MD82  M82  McDonnell Douglas MD-82
1         40374       M82  MD82  M82  McDonnell Douglas MD-82
2         31725       143  B463  143              BAe 146-300
3         48203       143  B463  143              BAe 146-300
4          2168       143  B463  143              BAe 146-300
...         ...       ...   ...  ...                      ...
74693     42650       SF3  SF34  SF3            Saab SF340A/B
74694      7818       SF3  SF34  SF3            Saab SF340A/B
74695     42616       SF3  SF34  SF3            Saab SF340A/B
74696     42727       SF3  SF34  SF3            Saab SF340A/B
74697     48922       SF3  SF34  SF3            Saab SF340A/B

[74698 rows x 5 columns]

##### Create the final tables (`Route_Equipment` and `Flight_Routes`)

In [96]:
%%bigquery
create or replace table air_travel_int.Route_Equipment as
    select re.route_id, a.icao as aircraft_icao
    from air_travel_int.tmp_route_equipment_unnested re join air_travel_int.Aircraft a
    on re.equipment = a.iata

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [52]:
%%bigquery
create or replace table air_travel_int.Flight_Routes as
    select route_id, airline_id, source_airport_icao, dest_airport_icao, codeshare, stops
    from air_travel_int.tmp_flight_routes_id

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Clean up

In [53]:
%%bigquery
drop table if exists air_travel_int.tmp_route_equipment;
drop table if exists air_travel_int.tmp_route_equipment_unnested;
drop table if exists air_travel_int.tmp_flight_routes;
drop table if exists air_travel_int.tmp_flight_routes_id;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### `Flight_Delays`

In [66]:
%%bigquery
select * from air_travel_stg.flight_delays
limit 10

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier carrier_name airport_code airport_city airport_state  \
0  2018-05-01      9K     Cape Air          GUM         Guam            TT   
1  2018-04-01      9K     Cape Air          GUM         Guam            TT   
2  2018-01-01      9K     Cape Air          GUM         Guam            TT   
3  2018-02-01      9K     Cape Air          GUM         Guam            TT   
4  2018-03-01      9K     Cape Air          GUM         Guam            TT   
5  2018-04-01      9K     Cape Air          SPN       Saipan            TT   
6  2018-02-01      9K     Cape Air          SPN       Saipan            TT   
7  2018-03-01      9K     Cape Air          SPN       Saipan            TT   
8  2018-05-01      9K     Cape Air          SPN       Saipan            TT   
9  2018-01-01      9K     Cape Air          SPN       Saipan            TT   

                             airport_name  arr_total  arr_cancelled  \
0                      Guam International        155              0   
1                      Guam International        150              0   
2                      Guam International        155              0   
3                      Guam International        140              1   
4                      Guam International        155              0   
5   Francisco C. Ada Saipan International        150              0   
6   Francisco C. Ada Saipan International        140              1   
7   Francisco C. Ada Saipan International        155              0   
8   Francisco C. Ada Saipan International        155              0   
9   Francisco C. Ada Saipan International        155              0   

   arr_diverted  arr_delay_min  weather_delay_min  nas_delay_min  \
0             0            394                  0             14   
1             0            664                 35             69   
2             0            710                  0             45   
3             0            330                  0              5   
4             0           1983                  0             83   
5             0            431                  0             56   
6             1            324                  0             68   
7             1           1128                  0            151   
8             1            269                  0             15   
9             1            687                  0             67   

   late_aircraft_delay_min _data_source                       _load_time  
0                      135    transtats 2024-08-25 15:45:31.691980+00:00  
1                      202    transtats 2024-08-25 15:45:31.691980+00:00  
2                      543    transtats 2024-08-25 15:45:31.691980+00:00  
3                      245    transtats 2024-08-25 15:45:31.691980+00:00  
4                     1225    transtats 2024-08-25 15:45:31.691980+00:00  
5                        0    transtats 2024-08-25 15:45:31.691980+00:00  
6                        0    transtats 2024-08-25 15:45:31.691980+00:00  
7                       10    transtats 2024-08-25 15:45:31.691980+00:00  
8                       50    transtats 2024-08-25 15:45:31.691980+00:00  
9                       24    transtats 2024-08-25 15:45:31.691980+00:00

In [72]:
%%bigquery
select event_month, carrier, airport_code, count(*) as count
from air_travel_stg.flight_delays
group by event_month, carrier, airport_code
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [event_month, carrier, airport_code, count]
Index: []

##### Standardize the airport and airline identifiers

##### Note: all carriers are present in the airline table

In [77]:
%%bigquery
select distinct airport_code, airport_city, airport_state, airport_name
from air_travel_stg.flight_delays
where airport_code not in (select iata from air_travel_int.Airport
                           where country = 'United States')

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [airport_code, airport_city, airport_state, airport_name]
Index: []

##### Note: all airports can be joined successfully

In [79]:
%%bigquery
select distinct fd.event_month, fd.carrier, fd.carrier_name, ap.icao as airport_icao,
    fd.arr_total, fd.arr_cancelled, fd.arr_diverted, fd.arr_delay_min,
    fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min,
from air_travel_stg.flight_delays fd join air_travel_int.Airport ap
on fd.airport_code = ap.iata
where ap.country = 'United States'

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier                               carrier_name  \
0       2023-10-01      MQ                                  Envoy Air   
1       2023-08-01      MQ                                  Envoy Air   
2       2023-11-01      MQ                                  Envoy Air   
3       2023-07-01      MQ                                  Envoy Air   
4       2023-09-01      MQ                                  Envoy Air   
...            ...     ...                                        ...   
376050  2018-07-01      C5  Commutair Aka Champlain Enterprises, Inc.   
376051  2018-06-01      C5  Commutair Aka Champlain Enterprises, Inc.   
376052  2018-08-01      C5  Commutair Aka Champlain Enterprises, Inc.   
376053  2018-09-01      C5  Commutair Aka Champlain Enterprises, Inc.   
376054  2018-10-01      C5  Commutair Aka Champlain Enterprises, Inc.   

       airport_icao  arr_total  arr_cancelled  arr_diverted  arr_delay_min  \
0              KBUR         32              0             0            284   
1              KBUR         27              0             1            152   
2              KBUR          4              0             0              0   
3              KBUR          3              0             0              0   
4              KBUR         33              0             0             42   
...             ...        ...            ...           ...            ...   
376050         KBWI         62              8             0           1122   
376051         KBWI         50              1             0           1677   
376052         KBWI         51              7             0           1688   
376053         KBWI         29              0             0            553   
376054         KBWI          3              0             0             86   

        weather_delay_min  nas_delay_min  late_aircraft_delay_min  
0                       0             27                        0  
1                       0              0                      152  
2                       0              0                        0  
3                       0              0                        0  
4                       0              0                       41  
...                   ...            ...                      ...  
376050                  0            531                      408  
376051                  0            532                      681  
376052                  0            330                      427  
376053                195            114                       64  
376054                  0              0                       80  

[376055 rows x 11 columns]

##### Materialize results to temp table

In [81]:
%%bigquery
create or replace table air_travel_int.tmp_flight_delays as
    select distinct fd.event_month, fd.carrier, fd.carrier_name, ap.icao as airport_icao,
        fd.arr_total, fd.arr_cancelled, fd.arr_diverted, fd.arr_delay_min,
        fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min,
    from air_travel_stg.flight_delays fd join air_travel_int.Airport ap
    on fd.airport_code = ap.iata
    where ap.country = 'United States'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

In [82]:
%%bigquery
select * from air_travel_int.tmp_flight_delays

Query is running:   0%|          |

Downloading:   0%|          |

event_month carrier                               carrier_name  \
0       2015-01-01      MQ                                  Envoy Air   
1       2020-04-01      MQ                                  Envoy Air   
2       2020-09-01      MQ                                  Envoy Air   
3       2018-07-01      MQ                                  Envoy Air   
4       2018-12-01      MQ                                  Envoy Air   
...            ...     ...                                        ...   
376050  2022-01-01      C5  Commutair Aka Champlain Enterprises, Inc.   
376051  2022-05-01      C5  Commutair Aka Champlain Enterprises, Inc.   
376052  2021-02-01      C5  Commutair Aka Champlain Enterprises, Inc.   
376053  2021-12-01      C5  Commutair Aka Champlain Enterprises, Inc.   
376054  2022-01-01      C5  Commutair Aka Champlain Enterprises, Inc.   

       airport_icao  arr_total  arr_cancelled  arr_diverted  arr_delay_min  \
0              KCID        282             21             1           7084   
1              KOKC         25             19             0              0   
2              KLCH         69             16             0            204   
3              KRIC        257             20             0           5289   
4              KORD       5747             95             8          67109   
...             ...        ...            ...           ...            ...   
376050         KALB         93             15             0           1541   
376051         KIAD        642             15             3          15799   
376052         KAMA         67             15             1            892   
376053         KIAD        610             15             0           9527   
376054         KROC         88             15             0           1838   

        weather_delay_min  nas_delay_min  late_aircraft_delay_min  
0                     984           1326                     2395  
1                       0              0                        0  
2                      55             42                        0  
3                     646           1382                     2474  
4                    3581          14423                    34235  
...                   ...            ...                      ...  
376050                  0            152                        0  
376051                792           3357                     6245  
376052                  0             54                      399  
376053                  1           1057                     5685  
376054                 93            246                      108  

[376055 rows x 11 columns]

In [87]:
%%bigquery
select distinct carrier, carrier_name
from air_travel_int.tmp_flight_delays
where carrier not in (select iata from air_travel_int.Airline
                      where country = 'United States')

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [carrier, carrier_name]
Index: []

In [90]:
%%bigquery
select fd.event_month, al.id as airline_id, fd.airport_icao, fd.arr_total, fd.arr_cancelled,
    fd.arr_diverted, fd.arr_delay_min, fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min
from air_travel_int.tmp_flight_delays fd join air_travel_int.Airline al
on fd.carrier = al.iata
where al.country = 'United States'

Query is running:   0%|          |

Downloading:   0%|          |

event_month  airline_id airport_icao  arr_total  arr_cancelled  \
0       2015-01-01         659         KCID        282             21   
1       2020-04-01         659         KOKC         25             19   
2       2020-09-01         659         KLCH         69             16   
3       2018-07-01         659         KRIC        257             20   
4       2018-12-01         659         KORD       5747             95   
...            ...         ...          ...        ...            ...   
381102  2022-01-01        1843         KALB         93             15   
381103  2022-05-01        1843         KIAD        642             15   
381104  2021-02-01        1843         KAMA         67             15   
381105  2021-12-01        1843         KIAD        610             15   
381106  2022-01-01        1843         KROC         88             15   

        arr_diverted  arr_delay_min  weather_delay_min  nas_delay_min  \
0                  1           7084                984           1326   
1                  0              0                  0              0   
2                  0            204                 55             42   
3                  0           5289                646           1382   
4                  8          67109               3581          14423   
...              ...            ...                ...            ...   
381102             0           1541                  0            152   
381103             3          15799                792           3357   
381104             1            892                  0             54   
381105             0           9527                  1           1057   
381106             0           1838                 93            246   

        late_aircraft_delay_min  
0                          2395  
1                             0  
2                             0  
3                          2474  
4                         34235  
...                         ...  
381102                        0  
381103                     6245  
381104                      399  
381105                     5685  
381106                      108  

[381107 rows x 10 columns]

##### Create final table

In [91]:
%%bigquery
create or replace table air_travel_int.Flight_Delays as
    select fd.event_month, al.id as airline_id, fd.airport_icao, fd.arr_total, fd.arr_cancelled,
        fd.arr_diverted, fd.arr_delay_min, fd.weather_delay_min, fd.nas_delay_min, fd.late_aircraft_delay_min
    from air_travel_int.tmp_flight_delays fd join air_travel_int.Airline al
    on fd.carrier = al.iata
    where al.country = 'United States'

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Check uniqueness of primary key fields

In [92]:
%%bigquery
select event_month, airline_id, airport_icao, count(*) as count
from air_travel_int.Flight_Delays
group by event_month, airline_id, airport_icao
having count(*) > 1

Query is running:   0%|          |

Downloading: |          |

Empty DataFrame
Columns: [event_month, airline_id, airport_icao, count]
Index: []

##### Clean up

In [93]:
%%bigquery
drop table if exists air_travel_int.tmp_flight_delays

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### Key Constraints
##### More details on how primary and foreign keys work in BQ: [link](https://cloud.google.com/blog/products/data-analytics/join-optimizations-with-bigquery-primary-and-foreign-keys?e=48754805)

##### Primary keys

In [2]:
%%bigquery
alter table air_travel_int.Aircraft add primary key (icao) not enforced;
alter table air_travel_int.Airline add primary key (id) not enforced;
alter table air_travel_int.Airport add primary key (icao) not enforced;
alter table air_travel_int.Airport_Businesses add primary key (icao, terminal, business, location) not enforced;
alter table air_travel_int.Airport_Review add primary key (id) not enforced;
alter table air_travel_int.Business add primary key (name) not enforced;
alter table air_travel_int.Country add primary key (name) not enforced;
alter table air_travel_int.Flight_Delays add primary key (event_month, airline_id, airport_icao) not enforced;
alter table air_travel_int.Flight_Routes add primary key (route_id) not enforced;
alter table air_travel_int.Menu_Items add primary key (business_name, menu_item) not enforced;
alter table air_travel_int.Route_Equipment add primary key (route_id, aircraft_icao) not enforced;
alter table air_travel_int.TSA_Traffic add primary key (event_date, event_hour, airport_icao, tsa_checkpoint) not enforced;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

##### Foreign keys

In [100]:
%%bigquery
alter table air_travel_int.Airline add constraint airline_fk_country foreign key (country)
    references air_travel_int.Country (name) not enforced;
alter table air_travel_int.Airport add constraint airport_fk_country foreign key (country)
    references air_travel_int.Country (name) not enforced;
alter table air_travel_int.Airport_Businesses add constraint airport_business_fk_icao foreign key (icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Airport_Review add constraint airport_reviews_fk_icao foreign key (icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Delays add constraint flight_delays_fk_airline_id foreign key (airline_id)
    references air_travel_int.Airline (id) not enforced;
alter table air_travel_int.Flight_Delays add constraint flight_delays_fk_airport_icao foreign key (airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_airline_id foreign key (airline_id)
    references air_travel_int.Airline (id) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_source_airport_icao foreign key (source_airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Flight_Routes add constraint flight_routes_fk_dest_airport_icao foreign key (dest_airport_icao)
    references air_travel_int.Airport (icao) not enforced;
alter table air_travel_int.Menu_Items add constraint menu_items_fk_business_name foreign key (business_name)
    references air_travel_int.Business (name) not enforced;
alter table air_travel_int.Route_Equipment add constraint route_equipment_fk_route_id foreign key (route_id)
    references air_travel_int.Flight_Routes (route_id) not enforced;
alter table air_travel_int.Route_Equipment add constraint route_equipment_fk_aircraft_icao foreign key (aircraft_icao)
    references air_travel_int.Aircraft (icao) not enforced;
alter table air_travel_int.TSA_Traffic add constraint tsa_traffic_fk_airport_icao foreign key (airport_icao)
    references air_travel_int.Airport (icao) not enforced;

Query is running:   0%|          |

Empty DataFrame
Columns: []
Index: []

#### Restart the runtime
##### Run this cell only if you see that code changes aren't getting picked up. Be sure to save your work before running.

In [ ]:
import os
os.kill(os.getpid(), 9)